# Capstone Project: Battle of the Neighborhoods
## From The Port in Cambridge, MA to Manhattan, NY
### by Arturo Avila-Lares

Due to the COVID-19 pandemic, a lot of people around the world have been forced to work from home. However, seeing as a lot of companies have determined that having employees work remotely is a feasible long-term option, a lot of people have moved from more expensive cities like New York—while saving in rent and maintaining their same jobs. Due to the decreased demand for real state, rent prices have reduced substantially so for a lot of people now would be a good opportunity to move to a city that they couldn’t afford pre-pandemic. According to Forbes, rent in New York City has dropped to 10-year lows. Rent in Manhattan has dropped 12.7%, which is more than the 10% drop that happened during the 2008 recession. This decrease has been propelled by an overall increase of 37,000 rentals.

For the purpose of this project, we are going to look at my particular case. I live in the city Cambridge, MA, which is adjacent to the city of Boston—more specifically, I live in a neighborhood called The Port (Zip Code 02139), Given that rent has decreased substantially in Manhattan and is now comparable to rent in the Cambridge/Boston area, I want to explore the idea of moving to a similar neighborhood in Manhattan. For that, I will be doing a K-means clustering analysis with neighborhoods in Boston and Cambridge to understand more about the type of neighborhood I live in. Then, I will proceed to do a clustering analysis with neighborhoods in Manhattan (my preferred borough in New York) to find a similar neighborhood to the one I currently live in and could potentially move to.

In [1]:
#Installing necessary packages
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


## Clustering Analysis No.1: Neighborhoods in the Cambridge/Boston, MA area

I will first be performing a K-means clustering analysis for neighborhoods in the Cambridge and Boston area together

### 1. Extracting and Cleaning Data for analysis

In [2]:
#Read CSV File containing a list of all neighborhoods in the Cambridge/Boston Area (CamBos)
Neigh=pd.read_csv('BostonNeighborhoods.csv')
Neigh.head()

Zip Code                                  Neighborhood
0      2101                               Downtown Boston
1      2108                                   Beacon Hill
2      2109                        Markets / Inner Harbor
3      2110                  Financial District / Wharves
4      2111  Chinatown / Tufts-New England Medical Center

In [3]:
#Open JSON file containing coordinates for all zip codes in the United States
with open('us-zip-code-latitude-and-longitude.json') as json_data:
    zipcodes = json.load(json_data)

In [4]:
zipcodes[0]

{'datasetid': 'us-zip-code-latitude-and-longitude',
 'recordid': 'f9c96aad055b64ae2582fc938bd46b024da05c46',
 'fields': {'city': 'Willow River',
  'zip': '55795',
  'dst': 1,
  'geopoint': [46.317812, -92.84315],
  'longitude': -92.84315,
  'state': 'MN',
  'latitude': 46.317812,
  'timezone': -6},
 'geometry': {'type': 'Point', 'coordinates': [-92.84315, 46.317812]},
 'record_timestamp': '2018-02-09T11:33:38.603-05:00'}

In [5]:
# define the dataframe columns
column_namesBoston = ['Zip Code', 'Latitude', 'Longitude'] 

# instantiate the dataframe
zipcodesDF = pd.DataFrame(columns=column_namesBoston)

In [6]:
zipcodesDF

Empty DataFrame
Columns: [Zip Code, Latitude, Longitude]
Index: []

In [7]:
for data in zipcodes:
    ZipCode = zipcodes_zip = data['fields']['zip'] 
    zipcodes_latitude = data['fields']['latitude']
    zipcodes_longitude = data['fields']['longitude']
    
    zipcodesDF = zipcodesDF.append({'Zip Code': ZipCode,
                                          'Latitude': zipcodes_latitude,
                                          'Longitude': zipcodes_longitude}, ignore_index=True)

In [8]:
zipcodesDF.head()

Zip Code   Latitude  Longitude
0    55795  46.317812  -92.84315
1    45388  40.328535  -84.47938
2    39483  31.218509  -89.90761
3    31503  31.205194  -82.37534
4    45833  40.841409  -84.34178

Now that I have the two data frames, I wanted to merge them to obtain one data fram with neighborhoods and coordinates. However, I ran into some issues because the zip code in one source was an object and an integer in the other so I converted both integers to be able to merge them

In [9]:
Neigh.dtypes

Zip Code         int64
Neighborhood    object
dtype: object

In [10]:
zipcodesDF.dtypes

Zip Code      object
Latitude     float64
Longitude    float64
dtype: object

In [11]:
zipcodesDF["Zip Code"] = zipcodesDF["Zip Code"].astype(str).astype(int)

In [12]:
zipcodesDF.dtypes

Zip Code       int64
Latitude     float64
Longitude    float64
dtype: object

In [13]:
Neigh1 = Neigh.merge(zipcodesDF, on='Zip Code', how='left')

In [14]:
Neigh1.head()

Zip Code                                  Neighborhood   Latitude  \
0      2101                               Downtown Boston  42.370567   
1      2108                                   Beacon Hill  42.357903   
2      2109                        Markets / Inner Harbor  42.361477   
3      2110                  Financial District / Wharves  42.356532   
4      2111  Chinatown / Tufts-New England Medical Center  42.349838   

   Longitude  
0 -71.026964  
1 -71.064080  
2 -71.054170  
3 -71.053650  
4 -71.061010

However, after merging I realized that the leading zero in the zip codes was gone because the column is an integer. Thus, I converted the column to a string (object) and added the leading zero.

In [15]:
Neigh1["Zip Code"] = Neigh1["Zip Code"].astype(str)

In [16]:
Neigh1.dtypes

Zip Code         object
Neighborhood     object
Latitude        float64
Longitude       float64
dtype: object

In [17]:
#Adding leading zero
Neigh1["Zip Code"] = Neigh1["Zip Code"].apply(lambda x: x.zfill(5))

In [18]:
Neigh1.head()

Zip Code                                  Neighborhood   Latitude  Longitude
0    02101                               Downtown Boston  42.370567 -71.026964
1    02108                                   Beacon Hill  42.357903 -71.064080
2    02109                        Markets / Inner Harbor  42.361477 -71.054170
3    02110                  Financial District / Wharves  42.356532 -71.053650
4    02111  Chinatown / Tufts-New England Medical Center  42.349838 -71.061010

### 2. Setting up API and exploring data in the map

In [19]:
#Getting location for Toronto
address = 'Cambridge, MA'

geolocator = Nominatim(user_agent="trt_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Cambridge are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Cambridge are 42.3750997, -71.1056157.


In [20]:
# create map of Toronto using latitude and longitude values
map_Cambridge = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood,zipcode in zip(Neigh1['Latitude'], Neigh1['Longitude'],Neigh1['Neighborhood'],Neigh1['Zip Code']):
    label = '{},{}'.format(neighborhood,zipcode)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Cambridge)  
    
map_Cambridge

In [21]:
#Foursquare API credentials
CLIENT_ID = 'WX0TFQX2BMUEPXYHYAPXLW4UJYYCTNFSVVNJL1PBSGA4K1DC' # your Foursquare ID
CLIENT_SECRET = 'PYILHVQOJFNN40GOBLPZPT3QCYCGX2ZIKE20JXYLEIERTLGM' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: WX0TFQX2BMUEPXYHYAPXLW4UJYYCTNFSVVNJL1PBSGA4K1DC
CLIENT_SECRET:PYILHVQOJFNN40GOBLPZPT3QCYCGX2ZIKE20JXYLEIERTLGM


In [22]:
#Exploring a neighborhood in Toronto
Neigh1.loc[0, 'Neighborhood']

'Downtown Boston'

In [23]:
#Using Cambridge's coordinates and crendential to set the request
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=WX0TFQX2BMUEPXYHYAPXLW4UJYYCTNFSVVNJL1PBSGA4K1DC&client_secret=PYILHVQOJFNN40GOBLPZPT3QCYCGX2ZIKE20JXYLEIERTLGM&v=20180605&ll=42.3750997,-71.1056157&radius=500&limit=100'

In [24]:
#Getting results
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '603df0a76f8cdb75ef5a921f'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': 'Mid-Cambridge',
  'headerFullLocation': 'Mid-Cambridge, Cambridge',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 38,
  'suggestedBounds': {'ne': {'lat': 42.3795997045, 'lng': -71.09953568279985},
   'sw': {'lat': 42.3705996955, 'lng': -71.11169571720015}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4a1c900cf964a520507b1fe3',
       'name': "Darwin's Ltd.",
       'location': {'address': '1629 Cambridge St',
        'crossStreet': 'Roberts Rd.',
        'lat': 42.374927661957294,
        'lng': -71.10939361557402,
        'labeledLatLngs': [{'label': 

In [25]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [26]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

<ipython-input-26-561c05f0fdd1>:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  nearby_venues = json_normalize(venues) # flatten JSON


name      categories        lat        lng
0               Darwin's Ltd.  Sandwich Place  42.374928 -71.109394
1          Whole Foods Market   Grocery Store  42.375879 -71.103184
2  Broadsheet Coffee Roasters     Coffee Shop  42.378039 -71.107275
3     Trina's Starlite Lounge             Bar  42.374480 -71.101671
4            Savenor's Market    Gourmet Shop  42.377968 -71.107461

In [27]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

38 venues were returned by Foursquare.


### 3. Exploring Neighborhoods in Cambridge/Boston

#### Writing function to get venues in these neighborhoods

In [28]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [29]:
BosCam_venues = getNearbyVenues(names=Neigh1['Neighborhood'],
                                   latitudes=Neigh1['Latitude'],
                                   longitudes=Neigh1['Longitude']
                                  )

Downtown Boston
Beacon Hill
Markets / Inner Harbor
Financial District / Wharves
Chinatown / Tufts-New England Medical Center
Downtown Boston
North End
West End / Back of the Hill
Fenway / East Fens / Longwood
Back Bay
Downtown Boston
South End
Roxbury
Roxbury Crossing
Roxbury / Grove Hall
Dorchester / Fields Corner
Downtown Boston
Dorchester / Codman Square
Dorchester / Uphams Corner
Mattapan
South Boston
East Boston
Charlestown
Jamaica Plain
Roslindale
West Roxbury
Downtown Boston
Allston
Brighton
Hyde Park
Readville
Mid Cambridge
The Port, Cambridge
North Cambridge
East Cambridge
Kendall Cambridge
Somerville
Somerville
Somerville
North Brighton / Cambridge
Downtown Boston
Prudential
Downtown Boston
Downtown Boston
South Boston / Fort Point
Kenmore / Boston University
Brookline
Brookline
Brookline Village


In [30]:
print(BosCam_venues.shape)
BosCam_venues.head()

(1802, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Downtown Boston              42.370567              -71.026964   
1  Downtown Boston              42.370567              -71.026964   
2  Downtown Boston              42.370567              -71.026964   
3  Downtown Boston              42.370567              -71.026964   
4  Downtown Boston              42.370567              -71.026964   

                       Venue  Venue Latitude  Venue Longitude  \
0           Alamo Rent A Car       42.368561       -71.029946   
1              Memorial Park       42.372588       -71.031452   
2        National Car Rental       42.368013       -71.030275   
3      Enterprise Rent-A-Car       42.368700       -71.029824   
4  Unified Rental Car Center       42.368447       -71.030115   

        Venue Category  
0  Rental Car Location  
1                 Park  
2  Rental Car Location  
3  Rental Car Location  
4  Rental Car Location

In [31]:
#Count of venues per neighborhood
BosCam_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                          
Allston                                                          75   
Back Bay                                                        100   
Beacon Hill                                                      81   
Brighton                                                         42   
Brookline                                                        80   
Brookline Village                                                 1   
Charlestown                                                      25   
Chinatown / Tufts-New England Medical Center                    100   
Dorchester / Codman Square                                       13   
Dorchester / Fields Corner                                       15   
Dorchester / Uphams Corner                                       17   
Downtown Boston                                                  98   
East Boston                                                      24   
East Cambridge                                                   38   
Fenway / East Fens / Longwood                                    34   
Financial District / Wharves                                     72   
Hyde Park                                                        16   
Jamaica Plain                                                    42   
Kendall Cambridge                                                57   
Kenmore / Boston University                                      61   
Markets / Inner Harbor                                          100   
Mattapan                                                         17   
Mid Cambridge                                                    10   
North Brighton / Cambridge                                       37   
North Cambridge                                                  18   
North End                                                        87   
Prudential                                                      100   
Readville                                                         1   
Roslindale                                                       27   
Roxbury                                                          10   
Roxbury / Grove Hall                                             12   
Roxbury Crossing                                                 17   
Somerville                                                      137   
South Boston                                                     29   
South Boston / Fort Point                                        68   
South End                                                        48   
The Port, Cambridge                                              40   
West End / Back of the Hill                                      39   
West Roxbury                                                     14   

                                              Neighborhood Longitude  Venue  \
Neighborhood                                                                  
Allston                                                           75     75   
Back Bay                                                         100    100   
Beacon Hill                                                       81     81   
Brighton                                                          42     42   
Brookline                                                         80     80   
Brookline Village                                                  1      1   
Charlestown                                                       25     25   
Chinatown / Tufts-New England Medical Center                     100    100   
Dorchester / Codman Square                                        13     13   
Dorchester / Fields Corner                                        15     15   
Dorchester / Uphams Corner                                        17     17   
Downtown Boston                                                   98     98   
East Boston                 

In [32]:
print('There are {} uniques categories.'.format(len(BosCam_venues['Venue Category'].unique())))

There are 253 uniques categories.


### 4. Preparing/Segmenting neighborhoods for clustering

In [33]:
# one hot encoding
BosCam_onehot = pd.get_dummies(BosCam_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
BosCam_onehot['Neighborhood'] = BosCam_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [BosCam_onehot.columns[-1]] + list(BosCam_onehot.columns[:-1])
BosCam_onehot = BosCam_onehot[fixed_columns]

BosCam_onehot.head()

Yoga Studio  Accessories Store  African Restaurant  Airport  \
0            0                  0                   0        0   
1            0                  0                   0        0   
2            0                  0                   0        0   
3            0                  0                   0        0   
4            0                  0                   0        0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  \
0                 0                    0             0         0   
1                 0                    0             0         0   
2                 0                    0             0         0   
3                 0                    0             0         0   
4                 0                    0             0         0   

   Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                 0            0           0                    0   
1                 0            0           0                    0   
2                 0            0           0                    0   
3                 0            0           0                    0   
4                 0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  Automotive Shop  \
0                 0                   0           0                0   
1                 0                   0           0                0   
2                 0                   0           0                0   
3                 0                   0           0                0   
4                 0                   0           0                0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Bed & Breakfast  Beer Bar  Beer Garden  Belgian Restaurant  Big Box Store  \
0                0         0            0                   0              0   
1                0         0            0                   0              0   
2                0         0            0                   0              0   
3                0         0            0                   0              0   
4                0         0            0                   0              0   

   Bike Rental / Bike Share  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0                         0           0              0          0         0   
1                         0           0              0          0         0   
2                         0           0              0          0         0   
3                         0           0              0          0         0   
4                         0           0              0          0         0   

   Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0                     0               0        0   
1              0                     0               0        0   
2              0                     0               0        0   
3              0                     0               0        0   
4              0                     0               0        0   

   Bubble Tea Shop  Burger Joint  Burrito Place  Bus Station  Bus Stop  \
0                0             0              0            0         0   
1                0             0              0            0         0   
2                0             0              0            0         0   
3                0             0              0            0         0   
4                0             0              0            0         0   

   Business Service  Cafeteria  Café  Caribbean Restaurant

In [34]:
BosCam_onehot.shape

(1802, 253)

In [35]:
BosCam_onehot_grouped = BosCam_onehot.groupby('Neighborhood').mean().reset_index()
BosCam_onehot_grouped

Neighborhood  Yoga Studio  \
0                                        Allston     0.000000   
1                                       Back Bay     0.000000   
2                                    Beacon Hill     0.012346   
3                                       Brighton     0.000000   
4                                      Brookline     0.012500   
5                              Brookline Village     0.000000   
6                                    Charlestown     0.080000   
7   Chinatown / Tufts-New England Medical Center     0.010000   
8                     Dorchester / Codman Square     0.076923   
9                     Dorchester / Fields Corner     0.000000   
10                    Dorchester / Uphams Corner     0.000000   
11                               Downtown Boston     0.000000   
12                                   East Boston     0.000000   
13                                East Cambridge     0.000000   
14                 Fenway / East Fens / Longwood     0.000000   
15                  Financial District / Wharves     0.000000   
16                                     Hyde Park     0.000000   
17                                 Jamaica Plain     0.047619   
18                             Kendall Cambridge     0.000000   
19                   Kenmore / Boston University     0.000000   
20                        Markets / Inner Harbor     0.010000   
21                                      Mattapan     0.000000   
22                                 Mid Cambridge     0.000000   
23                    North Brighton / Cambridge     0.000000   
24                               North Cambridge     0.000000   
25                                     North End     0.011494   
26                                    Prudential     0.010000   
27                                     Readville     0.000000   
28                                    Roslindale     0.000000   
29                                       Roxbury     0.000000   
30                          Roxbury / Grove Hall     0.000000   
31                              Roxbury Crossing     0.000000   
32                                    Somerville     0.021898   
33                                  South Boston     0.000000   
34                     South Boston / Fort Point     0.000000   
35                                     South End     0.020833   
36                           The Port, Cambridge     0.025000   
37                   West End / Back of the Hill     0.025641   
38                                  West Roxbury     0.000000   

    Accessories Store  African Restaurant   Airport  Airport Terminal  \
0            0.000000            0.000000  0.000000          0.000000   
1            0.010000            0.000000  0.000000          0.000000   
2            0.000000            0.000000  0.000000          0.000000   
3            0.000000            0.000000  0.000000          0.000000   
4            0.000000            0.000000  0.000000          0.000000   
5            0.000000            0.000000  0.000000          0.000000   
6            0.000000            0.000000  0.000000          0.000000   
7            0.000000            0.000000  0.000000          0.000000   
8            0.000000            0.000000  0.000000          0.000000   
9            0.000000            0.000000  0.000000          0.000000   
10           0.000000            0.000000  0.000000          0.000000   
11           0.000000            0.000000  0.010204          0.020408   
12           0.000000            0.000000  0.041667          0.000000   
13           0.000000            0.000000  0.000000          0.000000   
14           0.000000            0.000000  0.000000          0.000000   
15           0.000000            0.000000  0.000000          0.000000   
16           0.000000            0.000000  0.000000          0.000000   
17           0.047619            0.000000  0.000000          0.000000   
18           0.000000            0.000000  0.000

In [36]:
BosCam_onehot_grouped.shape

(39, 253)

In [37]:
num_top_venues = 5

for hood in BosCam_onehot_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = BosCam_onehot_grouped[BosCam_onehot_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allston----
                venue  freq
0   Korean Restaurant  0.08
1  Chinese Restaurant  0.04
2    Asian Restaurant  0.04
3    Sushi Restaurant  0.04
4     Thai Restaurant  0.04


----Back Bay----
                  venue  freq
0                   Spa  0.07
1                   Gym  0.04
2        Cosmetics Shop  0.04
3    Mexican Restaurant  0.03
4  Gym / Fitness Center  0.03


----Beacon Hill----
                     venue  freq
0              Coffee Shop  0.04
1     Gym / Fitness Center  0.04
2      American Restaurant  0.04
3            Historic Site  0.04
4  New American Restaurant  0.04


----Brighton----
                venue  freq
0                Bank  0.07
1              Bakery  0.07
2  Chinese Restaurant  0.07
3         Pizza Place  0.07
4         Bus Station  0.05


----Brookline----
              venue  freq
0       Pizza Place  0.05
1         Gift Shop  0.04
2              Park  0.04
3  Sushi Restaurant  0.04
4    Sandwich Place  0.02


----Brookline Village----
      

In [38]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [39]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = BosCam_onehot_grouped['Neighborhood']

for ind in np.arange(BosCam_onehot_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(BosCam_onehot_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0      Allston     Korean Restaurant      Asian Restaurant   
1     Back Bay                   Spa        Cosmetics Shop   
2  Beacon Hill    Italian Restaurant   American Restaurant   
3     Brighton    Chinese Restaurant                Bakery   
4    Brookline           Pizza Place      Sushi Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0      Sushi Restaurant                Bakery           Pizza Place   
1                   Gym                 Hotel    Seafood Restaurant   
2            Steakhouse            Restaurant         Historic Site   
3                  Bank           Pizza Place                  Café   
4             Gift Shop                  Park        Sandwich Place   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0       Thai Restaurant    Chinese Restaurant    Italian Restaurant   
1           Coffee Shop   American Restaurant        Sandwich Place   
2           Pizza Place  Gym / Fitness Center           Coffee Shop   
3                  Park           Bus Station                   Pub   
4                  Café                   Gym    Falafel Restaurant   

     9th Most Common Venue 10th Most Common Venue  
0      Fried Chicken Joint      Electronics Store  
1               Steakhouse   Gym / Fitness Center  
2  New American Restaurant      French Restaurant  
3              Dry Cleaner            Coffee Shop  
4      Japanese Restaurant             Donut Shop

### 5. Setting up clusters

In [40]:
# set number of clusters
kclusters = 10

BosCam_onehot_grouped_clustering = BosCam_onehot_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(BosCam_onehot_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 6, 6, 2, 2, 3, 6, 2, 9, 2], dtype=int32)

In [41]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

BosCam_merged_ = Neigh1

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
BosCam_merged_ = BosCam_merged_.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

BosCam_merged_.head() # check the last columns!

Zip Code                                  Neighborhood   Latitude  \
0    02101                               Downtown Boston  42.370567   
1    02108                                   Beacon Hill  42.357903   
2    02109                        Markets / Inner Harbor  42.361477   
3    02110                  Financial District / Wharves  42.356532   
4    02111  Chinatown / Tufts-New England Medical Center  42.349838   

   Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0 -71.026964               6      Business Service   Rental Car Location   
1 -71.064080               6    Italian Restaurant   American Restaurant   
2 -71.054170               5    Italian Restaurant    Seafood Restaurant   
3 -71.053650               6         Boat or Ferry       Harbor / Marina   
4 -71.061010               2    Chinese Restaurant                Bakery   

  3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
0                 Hotel   American Restaurant            Coffee Shop   
1            Steakhouse            Restaurant          Historic Site   
2                  Park                Bakery          Historic Site   
3                 Hotel         Historic Site               Aquarium   
4      Asian Restaurant      Sushi Restaurant  Performing Arts Venue   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0    Italian Restaurant            Food Truck     French Restaurant   
1           Pizza Place  Gym / Fitness Center           Coffee Shop   
2                  Café           Pizza Place                 Hotel   
3    Seafood Restaurant           Salad Place                  Park   
4   American Restaurant       Bubble Tea Shop                  Café   

     9th Most Common Venue 10th Most Common Venue  
0           Sandwich Place                 Bakery  
1  New American Restaurant      French Restaurant  
2            Grocery Store            Coffee Shop  
3      American Restaurant            Coffee Shop  
4              Coffee Shop              Hotel Bar

In [42]:
#Due to the merge, some rows had NaN 'Cluster Labels' so had to drop them to make map work
Toronto_BosCam_= BosCam_merged_.dropna()

In [43]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
# The code from the lab gave me some issues due to the clusters being floats so had to convert to integers
markers_colors = []
for lat, lon, poi, cluster in zip(BosCam_merged_['Latitude'], BosCam_merged_['Longitude'], BosCam_merged_['Neighborhood'], BosCam_merged_['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### 6. Evaluating clusters

In [44]:
#Cluster 1
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 0, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
12      Roxbury     Convenience Store   American Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
12                  Park                  Café      Business Service   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
12             BBQ Joint    African Restaurant  Fast Food Restaurant   

   9th Most Common Venue 10th Most Common Venue  
12          Food Service             Food Court

In [45]:
#Cluster 2
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 1, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
13  Roxbury Crossing           Pizza Place            Donut Shop   
33   North Cambridge           Pizza Place                   Spa   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
13      Italian Restaurant                 Track            Playground   
33  Furniture / Home Store        Farmers Market      Greek Restaurant   

      6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
13  New American Restaurant          Burger Joint       Bubble Tea Shop   
33       Mexican Restaurant        Clothing Store            Steakhouse   

        9th Most Common Venue 10th Most Common Venue  
13                        Gym           Liquor Store  
33  Middle Eastern Restaurant  Sri Lankan Restaurant

In [46]:
#Cluster 3
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 2, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood 1st Most Common Venue  \
4   Chinatown / Tufts-New England Medical Center    Chinese Restaurant   
15                    Dorchester / Fields Corner           Pizza Place   
18                    Dorchester / Uphams Corner                   Pub   
19                                      Mattapan          Home Service   
23                                 Jamaica Plain           Pizza Place   
27                                       Allston     Korean Restaurant   
28                                      Brighton    Chinese Restaurant   
36                                    Somerville           Pizza Place   
37                                    Somerville           Pizza Place   
38                                    Somerville           Pizza Place   
39                    North Brighton / Cambridge  Gym / Fitness Center   
46                                     Brookline           Pizza Place   
47                                     Brookline           Pizza Place   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
4                 Bakery      Asian Restaurant      Sushi Restaurant   
15         Women's Store              Pharmacy    Seafood Restaurant   
18           Pizza Place          Liquor Store                   Bar   
19           Pizza Place  Caribbean Restaurant            Nail Salon   
23                Bakery           Coffee Shop           Yoga Studio   
27      Asian Restaurant      Sushi Restaurant                Bakery   
28                Bakery                  Bank           Pizza Place   
36    Mexican Restaurant                  Park                  Café   
37    Mexican Restaurant                  Park                  Café   
38    Mexican Restaurant                  Park                  Café   
39                  Park           Pizza Place   Japanese Restaurant   
46      Sushi Restaurant             Gift Shop                  Park   
47      Sushi Restaurant             Gift Shop                  Park   

    5th Most Common Venue                     6th Most Common Venue  \
4   Performing Arts Venue                       American Restaurant   
15                   Bank                              Liquor Store   
18          Deli / Bodega                     Vietnamese Restaurant   
19                   Bank                                    Bakery   
23      Accessories Store                               Art Gallery   
27            Pizza Place                           Thai Restaurant   
28                   Café                                      Park   
36         Ice Cream Shop                         Indian Restaurant   
37         Ice Cream Shop                         Indian Restaurant   
38         Ice Cream Shop                         Indian Restaurant   
39    Fried Chicken Joint  Residential Building (Apartment / Condo)   
46         Sandwich Place                                      Café   
47         Sandwich Place                                      Café   

     7th Most Common Venue      8th Most Common Venue 9th Most Common Venue  \
4          Bubble Tea Shop                       Café           Coffee Shop   
15              Donut Shop                    Dog Run   Arts & Crafts Store   
18       Food & Drink Shop                Flower Shop    Chinese Restaurant   
19       Mobile Phone Shop          Food & Drink Shop         Hot Dog Joint   
23  Thrift / Vintage Store  Middle Eastern Restaurant             Bookstore   
27      Chinese Restaurant         Italian Restaurant   Fried Chicken Joint   
28             Bus Station                        Pub           Dry Cleaner   
36      Italian Restaurant                      Plaza            Donut Shop   
37      Italian Restaurant                      Plaza            Donut Shop   
38      Italian Restaurant                      Plaza            Donut Shop   
39               Cafeteria                        Bar        Lingerie Store   
46                     Gym         Falafel Rest

In [47]:
#Cluster 4
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 3, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
48  Brookline Village               Stables         Women's Store   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
48  Furniture / Home Store   Fried Chicken Joint     French Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
48            Food Truck          Food Service            Food Court   

   9th Most Common Venue 10th Most Common Venue  
48     Food & Drink Shop            Flower Shop

In [48]:
#Cluster 5
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 4, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
30    Readville      Business Service         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
30    Falafel Restaurant   Fried Chicken Joint     French Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
30            Food Truck          Food Service            Food Court   

   9th Most Common Venue 10th Most Common Venue  
30     Food & Drink Shop            Flower Shop

In [49]:
#Cluster 6
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 5, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
2   Markets / Inner Harbor    Italian Restaurant         Seafood Restaurant   
6                North End    Italian Restaurant                Pizza Place   
21             East Boston    Italian Restaurant  Latin American Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2                   Park                Bakery         Historic Site   
6     Seafood Restaurant           Coffee Shop                 Hotel   
21    Chinese Restaurant  Brazilian Restaurant                Bakery   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2                   Café           Pizza Place                 Hotel   
6         Sandwich Place                Bakery         Grocery Store   
21         Metro Station    Mexican Restaurant            Donut Shop   

   9th Most Common Venue 10th Most Common Venue  
2          Grocery Store            Coffee Shop  
6             Sports Bar                    Pub  
21   Peruvian Restaurant            Pizza Place

In [50]:
#Cluster 7
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 6, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood          1st Most Common Venue  \
0                 Downtown Boston               Business Service   
1                     Beacon Hill             Italian Restaurant   
3    Financial District / Wharves                  Boat or Ferry   
5                 Downtown Boston               Business Service   
7     West End / Back of the Hill            American Restaurant   
8   Fenway / East Fens / Longwood                     Art Museum   
9                        Back Bay                            Spa   
10                Downtown Boston               Business Service   
11                      South End                           Café   
16                Downtown Boston               Business Service   
20                   South Boston                    Coffee Shop   
22                    Charlestown                    Yoga Studio   
24                     Roslindale             Italian Restaurant   
26                Downtown Boston               Business Service   
29                      Hyde Park            American Restaurant   
31                  Mid Cambridge            American Restaurant   
32            The Port, Cambridge  Vegetarian / Vegan Restaurant   
34                 East Cambridge                  Grocery Store   
35              Kendall Cambridge                    Coffee Shop   
40                Downtown Boston               Business Service   
41                     Prudential                 Clothing Store   
42                Downtown Boston               Business Service   
43                Downtown Boston               Business Service   
44      South Boston / Fort Point                     Restaurant   
45    Kenmore / Boston University             Mexican Restaurant   

   2nd Most Common Venue 3rd Most Common Venue      4th Most Common Venue  \
0    Rental Car Location                 Hotel        American Restaurant   
1    American Restaurant            Steakhouse                 Restaurant   
3        Harbor / Marina                 Hotel              Historic Site   
5    Rental Car Location                 Hotel        American Restaurant   
7              Hotel Bar    Italian Restaurant                 Food Truck   
8            Pizza Place                Garden             Baseball Field   
9         Cosmetics Shop                   Gym                      Hotel   
10   Rental Car Location                 Hotel        American Restaurant   
11           Pizza Place                 Diner  Latin American Restaurant   
16   Rental Car Location                 Hotel        American Restaurant   
20           Pizza Place            Sports Bar         Italian Restaurant   
22     Convenience Store           Coffee Shop                Pizza Place   
24    Chinese Restaurant   American Restaurant                Pizza Place   
26   Rental Car Location                 Hotel        American Restaurant   
29        Clothing Store    Chinese Restaurant                       Park   
31    Italian Restaurant                 Hotel              Grocery Store   
32           Coffee Shop          Cocktail Bar                        Bar   
34     Convenience Store           Coffee Shop             Sandwich Place   
35                  Café   American Restaurant                 Food Truck   
40   Rental Car Location                 Hotel        American Restaurant   
41    Italian Restaurant           Coffee Shop             Ice Cream Shop   
42   Rental Car Location                 Hotel        American Restaurant   
43   Rental Car Location                 Hotel        American Restaurant   
44    Italian Restaurant                 Hotel                Coffee Shop   
45   American Restaurant                  Café                Coffee Shop   

       5th Most Common Venue    6th Most Common Venue  \
0                Coffee Shop       Italian Restaurant   
1              Historic Site              Pizza Place   
3                   Aquarium       Seafood Restaurant   
5                Coff

### The Port was placed in Cluster 7, which is characterized by having a lot of restaurants (from a wide array of cuisines) and fitness centers/gyms. It's a cluster that is likely to often receive out-of-town visitors as evidenced by the number of hotels and car rentals in the area, and the wide array of restaurants. A number of these neighborhoods have a considerable number of business centers, which may indicate the presence of offices, which can also be a reason for the number of restaurants, especially the many coffee shops.

### I knew a few of these as a someone who has been living in the area for 8 years, but it's interesting to see the analysis confirming what I already new. Plus, my old neighborhood 'Prudential' is in the same cluster, which in a way validates the analysis. I'm someone who likes to eat out often, goes to the gym, and likes living close to my place of work, and all of these are reflected in the cluster.

In [51]:
#Cluster 8
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 7, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
14  Roxbury / Grove Hall         Shopping Mall  Fast Food Restaurant   

   3rd Most Common Venue 4th Most Common Venue  \
14  Caribbean Restaurant            Donut Shop   

              5th Most Common Venue 6th Most Common Venue  \
14  Southern / Soul Food Restaurant        Cosmetics Shop   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
14             Nightclub           Supermarket        Clothing Store   

   10th Most Common Venue  
14               Pharmacy

In [52]:
#Cluster 9
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 8, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
25  West Roxbury         Grocery Store        Clothing Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
25         Train Station                  Park       Automotive Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
25          Liquor Store    Salon / Barbershop                   Gym   

   9th Most Common Venue 10th Most Common Venue  
25              Pharmacy            Pizza Place

In [53]:
#Cluster 10
BosCam_merged_.loc[BosCam_merged_['Cluster Labels'] == 9, BosCam_merged_.columns[[1] + list(range(5, BosCam_merged_.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
17  Dorchester / Codman Square         Deli / Bodega                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
17          Liquor Store            Restaurant              Pharmacy   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
17  Caribbean Restaurant        Farmers Market  Fast Food Restaurant   

   9th Most Common Venue 10th Most Common Venue  
17         Grocery Store   Gym / Fitness Center

### After trying different numbers of clusters, I settled for 10, which gave me clusters more similar in size. However, if I were to advance this analysis, I would consider using techniques to determine the optimal number of clusters.

## Clustering Analysis No.2: Neighborhoods in Manhattan, NY

Having finished the first analysis, I will be performing a K-means clustering analysis in Manhattan using the lab given in the module as reference, which will help me understand more about the neighborhoods in the area and could potentially be helpful if I decide to move to other neighborhoods in Manhattan in the future.

## 1. Download and Explore Dataset


Neighborhood has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood. 


#### Load and explore the data


Next, let's load the data.


In [54]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Notice how all the relevant data is in the _features_ key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.


In [55]:
neighborhoods_dataNYC = newyork_data['features']

Let's take a look at the first item in this list.


In [56]:
neighborhoods_dataNYC[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Tranform the data into a _pandas_ dataframe


The next task is essentially transforming this data of nested Python dictionaries into a _pandas_ dataframe. So let's start by creating an empty dataframe.


In [57]:
# define the dataframe columns
column_namesNYC = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoodsNYC = pd.DataFrame(columns=column_namesNYC)

Take a look at the empty dataframe to confirm that the columns are as intended.


In [58]:
neighborhoodsNYC

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.


In [59]:
for data in neighborhoods_dataNYC:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoodsNYC = neighborhoodsNYC.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe.


In [60]:
neighborhoodsNYC.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

And make sure that the dataset has all 5 boroughs and 306 neighborhoods.


In [61]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoodsNYC['Borough'].unique()),
        neighborhoodsNYC.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.


In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>ny_explorer</em>, as shown below.


In [62]:
addressNYC = 'New York City, NY'

geolocatorNYC = Nominatim(user_agent="ny_explorer")
locationNYC = geolocatorNYC.geocode(addressNYC)
latitudeNYC = locationNYC.latitude
longitudeNYC = locationNYC.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitudeNYC, longitudeNYC))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Create a map of New York with neighborhoods superimposed on top.


In [63]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitudeNYC, longitudeNYC], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoodsNYC['Latitude'], neighborhoodsNYC['Longitude'], neighborhoodsNYC['Borough'], neighborhoodsNYC['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [64]:
manhattan_data = neighborhoodsNYC[neighborhoodsNYC['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

Let's get the geographical coordinates of Manhattan.


In [65]:
addressNYC = 'Manhattan, NY'

geolocatorNYC = Nominatim(user_agent="ny_explorer")
locationNYC = geolocatorNYC.geocode(addressNYC)
latitudeNYC = locationNYC.latitude
longitudeNYC = locationNYC.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitudeNYC, longitudeNYC))

The geograpical coordinate of New York City are 40.7896239, -73.9598939.


As we did with all of New York City, let's visualize Manhattan the neighborhoods in it.


In [66]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitudeNYC, longitudeNYC], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.


#### Define Foursquare Credentials and Version


In [67]:
CLIENT_ID = 'WX0TFQX2BMUEPXYHYAPXLW4UJYYCTNFSVVNJL1PBSGA4K1DC' # your Foursquare ID
CLIENT_SECRET = 'PYILHVQOJFNN40GOBLPZPT3QCYCGX2ZIKE20JXYLEIERTLGM' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: WX0TFQX2BMUEPXYHYAPXLW4UJYYCTNFSVVNJL1PBSGA4K1DC
CLIENT_SECRET:PYILHVQOJFNN40GOBLPZPT3QCYCGX2ZIKE20JXYLEIERTLGM


#### Let's explore the first neighborhood in our dataframe.


Get the neighborhood's name.


In [68]:
manhattan_data.loc[0, 'Neighborhood']

'Marble Hill'

Get the neighborhood's latitude and longitude values.


In [69]:
neighborhood_latitude = manhattan_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = manhattan_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = manhattan_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Marble Hill are 40.87655077879964, -73.91065965862981.


#### Now, let's get the top 100 venues that are in Marble Hill within a radius of 500 meters.


First, let's create the GET request URL. Name your URL **url**.


In [70]:
# type your answer here
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=WX0TFQX2BMUEPXYHYAPXLW4UJYYCTNFSVVNJL1PBSGA4K1DC&client_secret=PYILHVQOJFNN40GOBLPZPT3QCYCGX2ZIKE20JXYLEIERTLGM&v=20180605&ll=40.87655077879964,-73.91065965862981&radius=500&limit=100'

Send the GET request and examine the resutls


In [71]:
results = requests.get(url).json()

From the Foursquare lab in the previous module, we know that all the information is in the _items_ key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.


In [72]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a _pandas_ dataframe.


In [73]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

<ipython-input-73-561c05f0fdd1>:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  nearby_venues = json_normalize(venues) # flatten JSON


name   categories        lat        lng
0       Arturo's  Pizza Place  40.874412 -73.910271
1    Bikram Yoga  Yoga Studio  40.876844 -73.906204
2  Tibbett Diner        Diner  40.880404 -73.908937
3        Dunkin'   Donut Shop  40.877136 -73.906666
4      Starbucks  Coffee Shop  40.877531 -73.905582

And how many venues were returned by Foursquare?


In [74]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

24 venues were returned by Foursquare.


<a id='item2'></a>


## 2. Explore Neighborhoods in Manhattan


#### Let's create a function to repeat the same process to all the neighborhoods in Manhattan


In [75]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called _manhattan_venues_.


In [76]:
# type your answer here
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


Double-click **here** for the solution.

<!-- The correct answer is:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )
--> 


#### Let's check the size of the resulting dataframe


In [77]:
print(manhattan_venues.shape)
manhattan_venues.head()

(3182, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066       Arturo's   
1  Marble Hill              40.876551               -73.91066    Bikram Yoga   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066        Dunkin'   
4  Marble Hill              40.876551               -73.91066      Starbucks   

   Venue Latitude  Venue Longitude Venue Category  
0       40.874412       -73.910271    Pizza Place  
1       40.876844       -73.906204    Yoga Studio  
2       40.880404       -73.908937          Diner  
3       40.877136       -73.906666     Donut Shop  
4       40.877531       -73.905582    Coffee Shop

Let's check how many venues were returned for each neighborhood


In [78]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       76                      76     76   
Carnegie Hill                           86                      86     86   
Central Harlem                          43                      43     43   
Chelsea                                100                     100    100   
Chinatown                              100                     100    100   
Civic Center                           100                     100    100   
Clinton                                100                     100    100   
East Harlem                             39                      39     39   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Gramercy                                83                      83     83   
Greenwich Village                      100                     100    100   
Hamilton Heights                        60                      60     60   
Hudson Yards                            69                      69     69   
Inwood                                  54                      54     54   
Lenox Hill                             100                     100    100   
Lincoln Square                          93                      93     93   
Little Italy                           100                     100    100   
Lower East Side                         49                      49     49   
Manhattan Valley                        40                      40     40   
Manhattanville                          47                      47     47   
Marble Hill                             24                      24     24   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                     42                      42     42   
Murray Hill                            100                     100    100   
Noho                                   100                     100    100   
Roosevelt Island                        27                      27     27   
Soho                                   100                     100    100   
Stuyvesant Town                         19                      19     19   
Sutton Place                           100                     100    100   
Tribeca                                 84                      84     84   
Tudor City                              77                      77     77   
Turtle Bay                             100                     100    100   
Upper East Side                        100                     100    100   
Upper West Side                         88                      88     88   
Washington Heights                      82                      82     82   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                76               76              76  
Carnegie Hill                    86               86              86  
Central Harlem                   43               43              43  
Chelsea                         100              100             100  
Chinatown                       100              100             100  
Civic Center                    100              100             100  
Clinton                         100              100             100  
East Harlem                      39               39              39  
East Village                    100              100             100  
Finan

#### Let's find out how many unique categories can be curated from all the returned venues


In [79]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 329 uniques categories.


## 3. Analyze Each Neighborhood


In [80]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Marble Hill                  0               0                  0   
1  Marble Hill                  0               0                  0   
2  Marble Hill                  0               0                  0   
3  Marble Hill                  0               0                  0   
4  Marble Hill                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arepa Restaurant  \
0                   0                    0             0                 0   
1                   0                    0             0                 0   
2                   0                    0             0                 0   
3                   0                    0             0                 0   
4                   0                    0             0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                    0          0           0           0       0     0    0   
1                    0          0           0           0       0     0    0   
2                    0          0           0           0       0     0    0   
3                    0          0           0           0       0     0    0   
4                    0          0           0           0       0     0    0   

   Basketball Court  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                 0         0            0           0              0   
1                 0         0            0           0              0   
2                 0         0            0           0              0   
3                 0         0            0           0              0   
4                 0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0              0          0         0           0                     0   
1              0          0         0           0                     0   
2              0          0         0           0                     0   
3              0          0         0           0                     0   
4              0          0         0           0                     0   

   Breakfast Spot  Bridal Shop  Bridge  Bubble Tea Shop  Building  \
0               0            0       0                0         0   
1               0            0       0                0         0   
2               0            0       0                0         0   
3               0            0       0                0         0   
4               0  

And let's examine the new dataframe size.


In [81]:
manhattan_onehot.shape

(3182, 330)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category


In [82]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City           0.000000        0.000000               0.00   
1         Carnegie Hill           0.000000        0.000000               0.00   
2        Central Harlem           0.000000        0.000000               0.00   
3               Chelsea           0.000000        0.000000               0.00   
4             Chinatown           0.000000        0.000000               0.00   
5          Civic Center           0.000000        0.000000               0.00   
6               Clinton           0.000000        0.000000               0.00   
7           East Harlem           0.000000        0.000000               0.00   
8          East Village           0.000000        0.000000               0.00   
9    Financial District           0.000000        0.000000               0.00   
10             Flatiron           0.000000        0.000000               0.00   
11             Gramercy           0.000000        0.000000               0.00   
12    Greenwich Village           0.010000        0.000000               0.00   
13     Hamilton Heights           0.000000        0.016667               0.00   
14         Hudson Yards           0.000000        0.000000               0.00   
15               Inwood           0.000000        0.000000               0.00   
16           Lenox Hill           0.000000        0.000000               0.01   
17       Lincoln Square           0.000000        0.000000               0.00   
18         Little Italy           0.000000        0.000000               0.00   
19      Lower East Side           0.000000        0.000000               0.00   
20     Manhattan Valley           0.000000        0.000000               0.00   
21       Manhattanville           0.000000        0.000000               0.00   
22          Marble Hill           0.000000        0.000000               0.00   
23              Midtown           0.000000        0.000000               0.00   
24        Midtown South           0.000000        0.000000               0.00   
25  Morningside Heights           0.000000        0.000000               0.00   
26          Murray Hill           0.000000        0.000000               0.00   
27                 Noho           0.000000        0.000000               0.00   
28     Roosevelt Island           0.000000        0.000000               0.00   
29                 Soho           0.000000        0.000000               0.00   
30      Stuyvesant Town           0.000000        0.000000               0.00   
31         Sutton Place           0.000000        0.010000               0.00   
32              Tribeca           0.000000        0.000000               0.00   
33           Tudor City           0.000000        0.000000               0.00   
34           Turtle Bay           0.000000        0.000000               0.00   
35      Upper East Side           0.000000        0.000000               0.00   
36      Upper West Side           0.011364        0.000000               0.00   
37   Washington Heights           0.012195        0.000000               0.00   
38         West Village           0.010000        0.010000               0.00   
39            Yorkville           0.000000        0.000000               0.00   

    African Restaurant  American Restaurant  Antique Shop  Arepa Restaurant  \
0             0.000000             0.013158          0.00          0.000000   
1             0.000000             0.011628          0.00          0.000000   
2             0.069767             0.046512          0.00          0.000000   
3             0.000000             0.040000          0.00          0.000000   
4             0.000000             0.040000          0.00          0.000000   
5             0.000000             0.040000          0.01          0.000000   
6             0.000000             0.040000          0.00          0.000000   
7             0.000000             0.000000          0.00

#### Let's confirm the new size


In [83]:
manhattan_grouped.shape

(40, 330)

#### Let's print each neighborhood along with the top 5 most common venues


In [84]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
            venue  freq
0     Coffee Shop  0.07
1            Park  0.05
2           Hotel  0.05
3  Clothing Store  0.05
4             Gym  0.05


----Carnegie Hill----
            venue  freq
0     Coffee Shop  0.08
1  Cosmetics Shop  0.05
2            Café  0.05
3     Yoga Studio  0.03
4       Bookstore  0.03


----Central Harlem----
                venue  freq
0  African Restaurant  0.07
1  Seafood Restaurant  0.05
2  Chinese Restaurant  0.05
3   French Restaurant  0.05
4      Cosmetics Shop  0.05


----Chelsea----
                 venue  freq
0          Art Gallery  0.06
1          Coffee Shop  0.05
2               Bakery  0.05
3  American Restaurant  0.04
4       Ice Cream Shop  0.03


----Chinatown----
                 venue  freq
0   Chinese Restaurant  0.08
1               Bakery  0.08
2  American Restaurant  0.04
3    Hotpot Restaurant  0.04
4         Cocktail Bar  0.04


----Civic Center----
                  venue  freq
0           Coffee Shop  0.08


#### Let's put that into a _pandas_ dataframe


Now let's create the new dataframe and display the top 10 venues for each neighborhood using the previously defined function.

In [85]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City           Coffee Shop                 Hotel   
1      Carnegie Hill           Coffee Shop        Cosmetics Shop   
2     Central Harlem    African Restaurant        Cosmetics Shop   
3            Chelsea           Art Gallery                Bakery   
4          Chinatown                Bakery    Chinese Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Park                   Gym        Clothing Store   
1                  Café           Yoga Studio           Pizza Place   
2                   Bar     French Restaurant   American Restaurant   
3           Coffee Shop   American Restaurant                 Hotel   
4          Cocktail Bar   American Restaurant     Hotpot Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Boat or Ferry         Memorial Site          Burger Joint   
1             Wine Shop                   Gym     French Restaurant   
2    Chinese Restaurant    Seafood Restaurant             Bookstore   
3        Ice Cream Shop    Seafood Restaurant    Italian Restaurant   
4          Dessert Shop    Salon / Barbershop                   Spa   

  9th Most Common Venue 10th Most Common Venue  
0                 Plaza            Beer Garden  
1             Bookstore           Cocktail Bar  
2  Ethiopian Restaurant       Tapas Restaurant  
3     French Restaurant                 Market  
4          Optical Shop     Mexican Restaurant

<a id='item4'></a>


## 4. Cluster Neighborhoods


Run _k_-means to cluster the neighborhood into 5 clusters.


In [86]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 0, 0, 0, 1, 1, 3, 0, 1], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.


In [87]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               1   
1  Manhattan           Chinatown  40.715618 -73.994279               0   
2  Manhattan  Washington Heights  40.851903 -73.936900               0   
3  Manhattan              Inwood  40.867684 -73.921210               3   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               3   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Discount Store           Coffee Shop        Sandwich Place   
1                Bakery    Chinese Restaurant          Cocktail Bar   
2                  Café                Bakery                  Bank   
3    Mexican Restaurant                Lounge            Restaurant   
4           Pizza Place           Coffee Shop                  Café   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                   Gym           Yoga Studio        Tennis Stadium   
1   American Restaurant     Hotpot Restaurant          Dessert Shop   
2     Mobile Phone Shop    Italian Restaurant         Deli / Bodega   
3                  Café    Chinese Restaurant              Wine Bar   
4    Mexican Restaurant         Deli / Bodega           Yoga Studio   

       7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0              Deli / Bodega      Department Store        Ice Cream Shop   
1         Salon / Barbershop                   Spa          Optical Shop   
2         Spanish Restaurant        Sandwich Place           Pizza Place   
3              Deli / Bodega           Pizza Place                Bakery   
4  Latin American Restaurant          Liquor Store                  Park   

  10th Most Common Venue  
0               Pharmacy  
1     Mexican Restaurant  
2                   Park  
3                   Park  
4           Cocktail Bar

Finally, let's visualize the resulting clusters


In [88]:
# create map
map_clusters = folium.Map(location=[latitudeNYC, longitudeNYC], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>


## 5. Examine Clusters


#### Cluster 1


In [89]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
1            Chinatown                Bakery       Chinese Restaurant   
2   Washington Heights                  Café                   Bakery   
5       Manhattanville    Seafood Restaurant              Coffee Shop   
6       Central Harlem    African Restaurant           Cosmetics Shop   
9            Yorkville    Italian Restaurant              Coffee Shop   
10          Lenox Hill    Italian Restaurant              Pizza Place   
12     Upper West Side                  Café       Italian Restaurant   
13      Lincoln Square                 Plaza                     Café   
17             Chelsea           Art Gallery                   Bakery   
18   Greenwich Village    Italian Restaurant           Clothing Store   
19        East Village                   Bar              Pizza Place   
20     Lower East Side    Chinese Restaurant                 Pharmacy   
22        Little Italy                Bakery                     Café   
23                Soho        Clothing Store       Italian Restaurant   
24        West Village    Italian Restaurant  New American Restaurant   
25    Manhattan Valley    Mexican Restaurant              Pizza Place   
31                Noho    Italian Restaurant              Art Gallery   

   3rd Most Common Venue     4th Most Common Venue  5th Most Common Venue  \
1           Cocktail Bar       American Restaurant      Hotpot Restaurant   
2                   Bank         Mobile Phone Shop     Italian Restaurant   
5       Sushi Restaurant        Mexican Restaurant     Chinese Restaurant   
6                    Bar         French Restaurant    American Restaurant   
9                    Bar                       Gym       Sushi Restaurant   
10           Coffee Shop              Cocktail Bar       Sushi Restaurant   
12                Bakery                       Bar               Wine Bar   
13          Concert Hall                   Theater  Performing Arts Venue   
17           Coffee Shop       American Restaurant                  Hotel   
18      Sushi Restaurant       American Restaurant      Indian Restaurant   
19          Cocktail Bar         Korean Restaurant     Italian Restaurant   
20                  Café               Pizza Place                 Bakery   
22       Bubble Tea Shop              Cocktail Bar     Chinese Restaurant   
23           Coffee Shop  Mediterranean Restaurant               Boutique   
24          Cocktail Bar       American Restaurant                   Park   
25                   Bar         Indian Restaurant            Coffee Shop   
31           Pizza Place         French Restaurant            Coffee Shop   

   6th Most Common Venue 7th Most Common Venue     8th Most Common Venue  \
1           Dessert Shop    Salon / Barbershop                       Spa   
2          Deli / Bodega    Spanish Restaurant            Sandwich Place   
5     Italian Restaurant      Ramen Restaurant          Cuban Restaurant   
6     Chinese Restaurant    Seafood Restaurant                 Bookstore   
9          Deli / Bodega             Wine Shop       Japanese Restaurant   
10          Burger Joint  Gym / Fitness Center                       Gym   
12           Pizza Place     Indian Restaurant               Coffee Shop   
13   Indie Movie Theater    Italian Restaurant                    Bakery   
17        Ice Cream Shop    Seafood Restaurant        Italian Restaurant   
18                   Gym              Boutique              Dessert Shop   
19              Wine Bar           Coffee Shop        Mexican Restaurant   
20           Art Gallery           Yoga Studio       Filipino Restaurant   
22           Coffee Shop              Tea Room  Mediterranean Restaurant   
23                Bakery    Seafood Restaurant        Salon / Barbershop   
24        Ice Cream Shop              Wine Bar                   Theater   
25         Grocery Store   Peruvian Restaurant              Noodle House   
31              

#### Cluster 2


In [90]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
0          Marble Hill        Discount Store              Coffee Shop   
8      Upper East Side               Exhibit       Italian Restaurant   
14             Clinton    Italian Restaurant     Gym / Fitness Center   
15             Midtown                 Hotel           Clothing Store   
16         Murray Hill           Coffee Shop                    Hotel   
21             Tribeca                  Park       Italian Restaurant   
27            Gramercy                   Bar       Italian Restaurant   
28   Battery Park City           Coffee Shop                    Hotel   
29  Financial District           Coffee Shop              Pizza Place   
30       Carnegie Hill           Coffee Shop           Cosmetics Shop   
32        Civic Center           Coffee Shop                      Spa   
34        Sutton Place    Italian Restaurant              Coffee Shop   
35          Turtle Bay    Italian Restaurant              Coffee Shop   
38            Flatiron    Italian Restaurant  New American Restaurant   
39        Hudson Yards  Gym / Fitness Center       Italian Restaurant   

   3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
0         Sandwich Place                     Gym           Yoga Studio   
8            Coffee Shop                  Bakery  Gym / Fitness Center   
14        Sandwich Place             Coffee Shop               Theater   
15               Theater     Sporting Goods Shop                   Spa   
16        Sandwich Place                     Bar   Japanese Restaurant   
21   American Restaurant             Coffee Shop              Wine Bar   
27           Pizza Place              Bagel Shop            Playground   
28                  Park                     Gym        Clothing Store   
29                   Bar            Cocktail Bar    Italian Restaurant   
30                  Café             Yoga Studio           Pizza Place   
32   American Restaurant            Cocktail Bar                 Hotel   
34                  Park    Gym / Fitness Center                   Gym   
35      Sushi Restaurant     Japanese Restaurant                  Park   
38   Japanese Restaurant  Furniture / Home Store                   Spa   
39   American Restaurant                    Café                 Hotel   

       6th Most Common Venue 7th Most Common Venue   8th Most Common Venue  \
0             Tennis Stadium         Deli / Bodega        Department Store   
8        American Restaurant                   Spa       French Restaurant   
14       American Restaurant                   Gym            Cocktail Bar   
15       American Restaurant           Coffee Shop                  Bakery   
16       American Restaurant          Burger Joint    Gym / Fitness Center   
21                       Spa                  Café          Scenic Lookout   
27        Mexican Restaurant           Coffee Shop  Thrift / Vintage Store   
28             Boat or Ferry         Memorial Site            Burger Joint   
29                Steakhouse                  Café     American Restaurant   
30                 Wine Shop                   Gym       French Restaurant   
32      Gym / Fitness Center     French Restaurant                    Park   
34    Furniture / Home Store   American Restaurant             Pizza Place   
35             Deli / Bodega    Seafood Restaurant        Ramen Restaurant   
38  Mediterranean Restaurant  Gym / Fitness Center             Coffee Shop   
39              Burger Joint            Restaurant             Coffee Shop   

   9th Most Common Venue 10th Most Common Venue  
0         Ice Cream Shop               Pharmacy  
8                  Hotel              Juice Bar  
14                   Spa              Wine Shop  
15        Sandwich Place              Bookstore  
16                Bakery      Jewish Restaurant  
21            Steakhouse             Poke Place  
27   American Restaurant         Pilates Studio  
28     

#### Cluster 3


In [91]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
1            Chinatown                Bakery       Chinese Restaurant   
2   Washington Heights                  Café                   Bakery   
5       Manhattanville    Seafood Restaurant              Coffee Shop   
6       Central Harlem    African Restaurant           Cosmetics Shop   
9            Yorkville    Italian Restaurant              Coffee Shop   
10          Lenox Hill    Italian Restaurant              Pizza Place   
12     Upper West Side                  Café       Italian Restaurant   
13      Lincoln Square                 Plaza                     Café   
17             Chelsea           Art Gallery                   Bakery   
18   Greenwich Village    Italian Restaurant           Clothing Store   
19        East Village                   Bar              Pizza Place   
20     Lower East Side    Chinese Restaurant                 Pharmacy   
22        Little Italy                Bakery                     Café   
23                Soho        Clothing Store       Italian Restaurant   
24        West Village    Italian Restaurant  New American Restaurant   
25    Manhattan Valley    Mexican Restaurant              Pizza Place   
31                Noho    Italian Restaurant              Art Gallery   

   3rd Most Common Venue     4th Most Common Venue  5th Most Common Venue  \
1           Cocktail Bar       American Restaurant      Hotpot Restaurant   
2                   Bank         Mobile Phone Shop     Italian Restaurant   
5       Sushi Restaurant        Mexican Restaurant     Chinese Restaurant   
6                    Bar         French Restaurant    American Restaurant   
9                    Bar                       Gym       Sushi Restaurant   
10           Coffee Shop              Cocktail Bar       Sushi Restaurant   
12                Bakery                       Bar               Wine Bar   
13          Concert Hall                   Theater  Performing Arts Venue   
17           Coffee Shop       American Restaurant                  Hotel   
18      Sushi Restaurant       American Restaurant      Indian Restaurant   
19          Cocktail Bar         Korean Restaurant     Italian Restaurant   
20                  Café               Pizza Place                 Bakery   
22       Bubble Tea Shop              Cocktail Bar     Chinese Restaurant   
23           Coffee Shop  Mediterranean Restaurant               Boutique   
24          Cocktail Bar       American Restaurant                   Park   
25                   Bar         Indian Restaurant            Coffee Shop   
31           Pizza Place         French Restaurant            Coffee Shop   

   6th Most Common Venue 7th Most Common Venue     8th Most Common Venue  \
1           Dessert Shop    Salon / Barbershop                       Spa   
2          Deli / Bodega    Spanish Restaurant            Sandwich Place   
5     Italian Restaurant      Ramen Restaurant          Cuban Restaurant   
6     Chinese Restaurant    Seafood Restaurant                 Bookstore   
9          Deli / Bodega             Wine Shop       Japanese Restaurant   
10          Burger Joint  Gym / Fitness Center                       Gym   
12           Pizza Place     Indian Restaurant               Coffee Shop   
13   Indie Movie Theater    Italian Restaurant                    Bakery   
17        Ice Cream Shop    Seafood Restaurant        Italian Restaurant   
18                   Gym              Boutique              Dessert Shop   
19              Wine Bar           Coffee Shop        Mexican Restaurant   
20           Art Gallery           Yoga Studio       Filipino Restaurant   
22           Coffee Shop              Tea Room  Mediterranean Restaurant   
23                Bakery    Seafood Restaurant        Salon / Barbershop   
24        Ice Cream Shop              Wine Bar                   Theater   
25         Grocery Store   Peruvian Restaurant              Noodle House   
31              

#### Cluster 4


In [92]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
3                Inwood    Mexican Restaurant                Lounge   
4      Hamilton Heights           Pizza Place           Coffee Shop   
7           East Harlem    Mexican Restaurant                Bakery   
11     Roosevelt Island                  Park     Food & Drink Shop   
26  Morningside Heights                  Park             Bookstore   
36           Tudor City                  Park    Mexican Restaurant   

                       3rd Most Common Venue 4th Most Common Venue  \
3                                 Restaurant                  Café   
4                                       Café    Mexican Restaurant   
7                            Thai Restaurant         Deli / Bodega   
11  Residential Building (Apartment / Condo)        Sandwich Place   
26                       American Restaurant           Coffee Shop   
36                                      Café                 Diner   

        5th Most Common Venue 6th Most Common Venue  \
3          Chinese Restaurant              Wine Bar   
4               Deli / Bodega           Yoga Studio   
7   Latin American Restaurant        Sandwich Place   
11                Supermarket           Coffee Shop   
26                       Café          Burger Joint   
36              Deli / Bodega                   Gym   

        7th Most Common Venue 8th Most Common Venue  9th Most Common Venue  \
3               Deli / Bodega           Pizza Place                 Bakery   
4   Latin American Restaurant          Liquor Store                   Park   
7                        Café          Liquor Store             Taco Place   
11               Liquor Store          Soccer Field       Greek Restaurant   
26             Sandwich Place    Mexican Restaurant           Tennis Court   
36                Coffee Shop      Greek Restaurant  Vietnamese Restaurant   

   10th Most Common Venue  
3                    Park  
4            Cocktail Bar  
7             Gas Station  
11         Farmers Market  
26           Liquor Store  
36                 Garden

#### Cluster 5


In [93]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
33  Midtown South     Korean Restaurant                 Hotel   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
33             Hotel Bar   Japanese Restaurant          Dessert Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
33        Cosmetics Shop           Coffee Shop    Italian Restaurant   

   9th Most Common Venue 10th Most Common Venue  
33             Gastropub   Gym / Fitness Center

#### Given that this analysis was provided by Coursera, it seems like the number of clusters is optimal.

## Clustering Analysis No.3: Neighborhoods in Cambridge/Boston and Manhattan

## 1. Prepare data


Now that I have explored neighborhoods in both places, I want to cluster all neighborhoods and see which Manhattan neighborhoods are in the same cluster as The Port in Cambridge.

In [94]:
#Concatenating venues in both locations
Man_BosCam_venues = pd.concat([BosCam_venues, manhattan_venues], ignore_index=True, sort=False)
Man_BosCam_venues

Neighborhood  Neighborhood Latitude  \
0                                  Downtown Boston              42.370567   
1                                  Downtown Boston              42.370567   
2                                  Downtown Boston              42.370567   
3                                  Downtown Boston              42.370567   
4                                  Downtown Boston              42.370567   
5                                  Downtown Boston              42.370567   
6                                  Downtown Boston              42.370567   
7                                  Downtown Boston              42.370567   
8                                  Downtown Boston              42.370567   
9                                  Downtown Boston              42.370567   
10                                 Downtown Boston              42.370567   
11                                 Downtown Boston              42.370567   
12                                 Downtown Boston              42.370567   
13                                 Downtown Boston              42.370567   
14                                 Downtown Boston              42.370567   
15                                 Downtown Boston              42.370567   
16                                 Downtown Boston              42.370567   
17                                 Downtown Boston              42.370567   
18                                 Downtown Boston              42.370567   
19                                 Downtown Boston              42.370567   
20                                 Downtown Boston              42.370567   
21                                     Beacon Hill              42.357903   
22                                     Beacon Hill              42.357903   
23                                     Beacon Hill              42.357903   
24                                     Beacon Hill              42.357903   
25                                     Beacon Hill              42.357903   
26                                     Beacon Hill              42.357903   
27                                     Beacon Hill              42.357903   
28                                     Beacon Hill              42.357903   
29                                     Beacon Hill              42.357903   
30                                     Beacon Hill              42.357903   
31                                     Beacon Hill              42.357903   
32                                     Beacon Hill              42.357903   
33                                     Beacon Hill              42.357903   
34                                     Beacon Hill              42.357903   
35                                     Beacon Hill              42.357903   
36                                     Beacon Hill              42.357903   
37                                     Beacon Hill              42.357903   
38                                     Beacon Hill              42.357903   
39                                     Beacon Hill              42.357903   
40                                     Beacon Hill              42.357903   
41                                     Beacon Hill              42.357903   
42                                     Beacon Hill              42.357903   
43                                     Beacon Hill              42.357903   
44                                     Beacon Hill              42.357903   
45                                     Beacon Hill              42.357903   
46                                     Beacon Hill              42.357903   
47                                     Beacon Hill              42.357903   
48                                     Beacon Hill              42.357903   
49                                     Beacon Hill              42.357903   
50                                     Beacon Hill              42.357903   
51                                

#### Let's find out how many unique categories can be curated from all the returned venues


In [95]:
print('There are {} uniques categories.'.format(len(Man_BosCam_venues['Venue Category'].unique())))

There are 376 uniques categories.


## 2. Analyze Each Neighborhood

In [96]:
# one hot encoding
Man_BosCam_onehot = pd.get_dummies(Man_BosCam_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Man_BosCam_onehot['Neighborhood'] = Man_BosCam_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Man_BosCam_onehot.columns[-1]] + list(Man_BosCam_onehot.columns[:-1])
Man_BosCam_onehot = Man_BosCam_onehot[fixed_columns]

Man_BosCam_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport  Airport Terminal  American Restaurant  \
0                   0        0                 0                    0   
1                   0        0                 0                    0   
2                   0        0                 0                    0   
3                   0        0                 0                    0   
4                   0        0                 0                    0   

   Antique Shop  Aquarium  Arepa Restaurant  Argentinian Restaurant  \
0             0         0                 0                       0   
1             0         0                 0                       0   
2             0         0                 0                       0   
3             0         0                 0                       0   
4             0         0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0            0           0                    0                 0   
1            0           0                    0                 0   
2            0           0                    0                 0   
3            0           0                    0                 0   
4            0           0                    0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                0          0           0           0       0     0    0   
1                0          0           0           0       0     0    0   
2                0          0           0           0       0     0    0   
3                0          0           0           0       0     0    0   
4                0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Bed & Breakfast  \
0               0                 0                 0                0   
1               0                 0                 0                0   
2               0                 0                 0                0   
3               0                 0                 0                0   
4               0                 0                 0                0   

   Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  Big Box Store  \
0         0            0           0                   0              0   
1         0            0           0                   0              0   
2         0            0           0                   0              0   
3         0            0           0                   0              0   
4         0            0           0                   0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   B

And let's examine the new dataframe size.


In [97]:
Man_BosCam_onehot.shape

(4984, 376)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category


In [98]:
Man_BosCam_grouped = Man_BosCam_onehot.groupby('Neighborhood').mean().reset_index()
Man_BosCam_grouped

Neighborhood  Yoga Studio  \
0                                        Allston     0.000000   
1                                       Back Bay     0.000000   
2                              Battery Park City     0.000000   
3                                    Beacon Hill     0.012346   
4                                       Brighton     0.000000   
5                                      Brookline     0.012500   
6                              Brookline Village     0.000000   
7                                  Carnegie Hill     0.034884   
8                                 Central Harlem     0.000000   
9                                    Charlestown     0.080000   
10                                       Chelsea     0.010000   
11                                     Chinatown     0.000000   
12  Chinatown / Tufts-New England Medical Center     0.010000   
13                                  Civic Center     0.030000   
14                                       Clinton     0.000000   
15                    Dorchester / Codman Square     0.076923   
16                    Dorchester / Fields Corner     0.000000   
17                    Dorchester / Uphams Corner     0.000000   
18                               Downtown Boston     0.000000   
19                                   East Boston     0.000000   
20                                East Cambridge     0.000000   
21                                   East Harlem     0.000000   
22                                  East Village     0.000000   
23                 Fenway / East Fens / Longwood     0.000000   
24                            Financial District     0.000000   
25                  Financial District / Wharves     0.000000   
26                                      Flatiron     0.020000   
27                                      Gramercy     0.012048   
28                             Greenwich Village     0.010000   
29                              Hamilton Heights     0.033333   
30                                  Hudson Yards     0.000000   
31                                     Hyde Park     0.000000   
32                                        Inwood     0.018519   
33                                 Jamaica Plain     0.047619   
34                             Kendall Cambridge     0.000000   
35                   Kenmore / Boston University     0.000000   
36                                    Lenox Hill     0.010000   
37                                Lincoln Square     0.010753   
38                                  Little Italy     0.010000   
39                               Lower East Side     0.020408   
40                              Manhattan Valley     0.025000   
41                                Manhattanville     0.000000   
42                                   Marble Hill     0.041667   
43                        Markets / Inner Harbor     0.010000   
44                                      Mattapan     0.000000   
45                                 Mid Cambridge     0.000000   
46                                       Midtown     0.000000   
47                                 Midtown South     0.010000   
48                           Morningside Heights     0.000000   
49                                   Murray Hill     0.010000   
50                                          Noho     0.010000   
51                    North Brighton / Cambridge     0.000000   
52                               North Cambridge     0.000000   
53                                     North End     0.011494   
54                                    Prudential     0.010000   
55                                     Readville     0.000000   
56                              Roosevelt Island     0.000000   
57                                    Roslindale     0.000000   
58                                       Roxbury     0.000000   
59                          Roxbury / Grove Hall     0.000000   
60                              Roxbury Crossing     0.000000   
61    

#### Let's confirm the new size


In [99]:
Man_BosCam_grouped.shape

(79, 376)

#### Let's print each neighborhood along with the top 5 most common venues


In [100]:
num_top_venues = 5

for hood in Man_BosCam_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = Man_BosCam_grouped[Man_BosCam_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allston----
                venue  freq
0   Korean Restaurant  0.08
1     Thai Restaurant  0.04
2  Chinese Restaurant  0.04
3    Asian Restaurant  0.04
4              Bakery  0.04


----Back Bay----
                  venue  freq
0                   Spa  0.07
1        Cosmetics Shop  0.04
2                   Gym  0.04
3    Mexican Restaurant  0.03
4  Gym / Fitness Center  0.03


----Battery Park City----
            venue  freq
0     Coffee Shop  0.07
1  Clothing Store  0.05
2             Gym  0.05
3           Hotel  0.05
4            Park  0.05


----Beacon Hill----
                  venue  freq
0            Restaurant  0.04
1    Italian Restaurant  0.04
2           Coffee Shop  0.04
3           Pizza Place  0.04
4  Gym / Fitness Center  0.04


----Brighton----
                venue  freq
0                Bank  0.07
1         Pizza Place  0.07
2  Chinese Restaurant  0.07
3              Bakery  0.07
4         Dry Cleaner  0.05


----Brookline----
                 venue  freq
0      

                 venue  freq
0  American Restaurant   0.2
1        Historic Site   0.1
2                Hotel   0.1
3               Bakery   0.1
4   Italian Restaurant   0.1


----Midtown----
                 venue  freq
0                Hotel  0.09
1       Clothing Store  0.05
2              Theater  0.04
3  Sporting Goods Shop  0.04
4       Sandwich Place  0.03


----Midtown South----
                 venue  freq
0    Korean Restaurant  0.21
1                Hotel  0.06
2            Hotel Bar  0.05
3  Japanese Restaurant  0.04
4          Coffee Shop  0.03


----Morningside Heights----
                 venue  freq
0                 Park  0.10
1          Coffee Shop  0.07
2            Bookstore  0.07
3  American Restaurant  0.07
4                 Café  0.05


----Murray Hill----
                 venue  freq
0          Coffee Shop  0.06
1                Hotel  0.05
2       Sandwich Place  0.05
3  Japanese Restaurant  0.04
4                  Bar  0.04


----Noho----
                venue

Now let's create the new dataframe and display the top 10 venues for each neighborhood.


In [101]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
Man_BosCam_venues_sorted = pd.DataFrame(columns=columns)
Man_BosCam_venues_sorted['Neighborhood'] = Man_BosCam_grouped['Neighborhood']

for ind in np.arange(Man_BosCam_grouped.shape[0]):
    Man_BosCam_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Man_BosCam_grouped.iloc[ind, :], num_top_venues)

Man_BosCam_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0            Allston     Korean Restaurant       Thai Restaurant   
1           Back Bay                   Spa                   Gym   
2  Battery Park City           Coffee Shop        Clothing Store   
3        Beacon Hill   American Restaurant  Gym / Fitness Center   
4           Brighton                Bakery           Pizza Place   

  3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
0                Bakery              Pizza Place      Asian Restaurant   
1        Cosmetics Shop              Coffee Shop        Sandwich Place   
2                   Gym                     Park                 Hotel   
3            Steakhouse  New American Restaurant         Historic Site   
4                  Bank       Chinese Restaurant                   Pub   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0      Sushi Restaurant    Chinese Restaurant   Fried Chicken Joint   
1            Steakhouse    Mexican Restaurant                 Hotel   
2         Boat or Ferry         Memorial Site             BBQ Joint   
3           Pizza Place    Italian Restaurant            Restaurant   
4                  Café                  Park           Dry Cleaner   

  9th Most Common Venue 10th Most Common Venue  
0              Pharmacy      Electronics Store  
1  Gym / Fitness Center     Seafood Restaurant  
2        Sandwich Place          Shopping Mall  
3           Coffee Shop     Falafel Restaurant  
4           Bus Station          Metro Station

In [102]:
#I needed to easily distinguish between neighboorhoods in both locastions so I added a column with the state
Neigh2 = Neigh1.drop('Zip Code',1)
Neigh2['State'] = 'MA'
manhattan_data2 = manhattan_data.drop('Borough',1)
manhattan_data2['State'] = 'NY'
Man_BosCam = pd.concat([Neigh2,manhattan_data2], ignore_index=True, sort=False)
Man_BosCam

Neighborhood   Latitude  Longitude State
0                                Downtown Boston  42.370567 -71.026964    MA
1                                    Beacon Hill  42.357903 -71.064080    MA
2                         Markets / Inner Harbor  42.361477 -71.054170    MA
3                   Financial District / Wharves  42.356532 -71.053650    MA
4   Chinatown / Tufts-New England Medical Center  42.349838 -71.061010    MA
5                                Downtown Boston  42.338947 -70.919635    MA
6                                      North End  42.365028 -71.056360    MA
7                    West End / Back of the Hill  42.361792 -71.067740    MA
8                  Fenway / East Fens / Longwood  42.343080 -71.092680    MA
9                                       Back Bay  42.349622 -71.073720    MA
10                               Downtown Boston  42.338947 -70.919635    MA
11                                     South End  42.338724 -71.072760    MA
12                                       Roxbury  42.324511 -71.084550    MA
13                              Roxbury Crossing  42.332099 -71.096510    MA
14                          Roxbury / Grove Hall  42.307448 -71.081270    MA
15                    Dorchester / Fields Corner  42.296298 -71.054540    MA
16                               Downtown Boston  42.338947 -70.919635    MA
17                    Dorchester / Codman Square  42.287130 -71.071560    MA
18                    Dorchester / Uphams Corner  42.316852 -71.058110    MA
19                                      Mattapan  42.272098 -71.094260    MA
20                                  South Boston  42.334990 -71.045620    MA
21                                   East Boston  42.378297 -71.025500    MA
22                                   Charlestown  42.378619 -71.064950    MA
23                                 Jamaica Plain  42.309998 -71.111710    MA
24                                    Roslindale  42.284678 -71.130520    MA
25                                  West Roxbury  42.279432 -71.159800    MA
26                               Downtown Boston  42.338947 -70.919635    MA
27                                       Allston  42.355147 -71.131640    MA
28                                      Brighton  42.348418 -71.153490    MA
29                                     Hyde Park  42.252198 -71.125930    MA
30                                     Readville  42.338947 -70.919635    MA
31                                 Mid Cambridge  42.379146 -71.128030    MA
32                           The Port, Cambridge  42.364347 -71.104310    MA
33                               North Cambridge  42.393327 -71.128370    MA
34                                East Cambridge  42.370519 -71.084430    MA
35                             Kendall Cambridge  42.362297 -71.084120    MA
36                                    Somerville  42.381929 -71.099080    MA
37                                    Somerville  42.399546 -71.121650    MA
38                                    Somerville  42.390846 -71.092250    MA
39                    North Brighton / Cambridge  42.367946 -71.120560    MA
40                               Downtown Boston  42.338947 -70.919635    MA
41                                    Prudential  42.347130 -71.082340    MA
42                               Downtown Boston  42.338947 -70.919635    MA
43                               Downtown Boston  42.350334 -71.053877    MA
44                     South Boston / Fort Point  42.347974 -71.044630    MA
45                   Kenmore / Boston University  42.346997 -71.102150    MA
46                                     Brookline  42.324397 -71.139330    MA
47                                     Brookline  42.344747 -71.121410    MA
48                             Brookline Village  42.180048 -71.089230    MA
49                                   Marble Hill  40.876551 -73.910660    NY
50                                     Chinatown  40.715618 -73.994279    NY
51                            Wa

## 3. Set up clusters

In [103]:
# set number of clusters
kclusters = 10

Man_BosCam_grouped_clustering = Man_BosCam_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Man_BosCam_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 8, 8, 8, 1, 1, 2, 8, 8, 5], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.


In [104]:
# add clustering labels
Man_BosCam_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Man_BosCam_merged = Man_BosCam

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
Man_BosCam_merged = Man_BosCam_merged.join(Man_BosCam_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

Man_BosCam_merged.head() # check the last columns!

Neighborhood   Latitude  Longitude State  \
0                               Downtown Boston  42.370567 -71.026964    MA   
1                                   Beacon Hill  42.357903 -71.064080    MA   
2                        Markets / Inner Harbor  42.361477 -71.054170    MA   
3                  Financial District / Wharves  42.356532 -71.053650    MA   
4  Chinatown / Tufts-New England Medical Center  42.349838 -71.061010    MA   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               8      Business Service   Rental Car Location   
1               8   American Restaurant  Gym / Fitness Center   
2               7    Italian Restaurant    Seafood Restaurant   
3               8         Boat or Ferry       Harbor / Marina   
4               1    Chinese Restaurant                Bakery   

  3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop      American Restaurant                 Hotel   
1            Steakhouse  New American Restaurant         Historic Site   
2                Bakery                     Park         Historic Site   
3                 Hotel                 Aquarium         Historic Site   
4      Asian Restaurant         Sushi Restaurant             Hotel Bar   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0             Food Truck    Italian Restaurant                Bakery   
1            Pizza Place    Italian Restaurant            Restaurant   
2                   Café           Pizza Place        Sandwich Place   
3            Salad Place    Seafood Restaurant                  Park   
4  Performing Arts Venue           Coffee Shop               Theater   

  9th Most Common Venue      10th Most Common Venue  
0        Sandwich Place           French Restaurant  
1           Coffee Shop          Falafel Restaurant  
2                 Hotel  Tourist Information Center  
3                Bakery                 Coffee Shop  
4                  Café         American Restaurant

In [105]:
Man_BosCam_merged

Neighborhood   Latitude  Longitude State  \
0                                Downtown Boston  42.370567 -71.026964    MA   
1                                    Beacon Hill  42.357903 -71.064080    MA   
2                         Markets / Inner Harbor  42.361477 -71.054170    MA   
3                   Financial District / Wharves  42.356532 -71.053650    MA   
4   Chinatown / Tufts-New England Medical Center  42.349838 -71.061010    MA   
5                                Downtown Boston  42.338947 -70.919635    MA   
6                                      North End  42.365028 -71.056360    MA   
7                    West End / Back of the Hill  42.361792 -71.067740    MA   
8                  Fenway / East Fens / Longwood  42.343080 -71.092680    MA   
9                                       Back Bay  42.349622 -71.073720    MA   
10                               Downtown Boston  42.338947 -70.919635    MA   
11                                     South End  42.338724 -71.072760    MA   
12                                       Roxbury  42.324511 -71.084550    MA   
13                              Roxbury Crossing  42.332099 -71.096510    MA   
14                          Roxbury / Grove Hall  42.307448 -71.081270    MA   
15                    Dorchester / Fields Corner  42.296298 -71.054540    MA   
16                               Downtown Boston  42.338947 -70.919635    MA   
17                    Dorchester / Codman Square  42.287130 -71.071560    MA   
18                    Dorchester / Uphams Corner  42.316852 -71.058110    MA   
19                                      Mattapan  42.272098 -71.094260    MA   
20                                  South Boston  42.334990 -71.045620    MA   
21                                   East Boston  42.378297 -71.025500    MA   
22                                   Charlestown  42.378619 -71.064950    MA   
23                                 Jamaica Plain  42.309998 -71.111710    MA   
24                                    Roslindale  42.284678 -71.130520    MA   
25                                  West Roxbury  42.279432 -71.159800    MA   
26                               Downtown Boston  42.338947 -70.919635    MA   
27                                       Allston  42.355147 -71.131640    MA   
28                                      Brighton  42.348418 -71.153490    MA   
29                                     Hyde Park  42.252198 -71.125930    MA   
30                                     Readville  42.338947 -70.919635    MA   
31                                 Mid Cambridge  42.379146 -71.128030    MA   
32                           The Port, Cambridge  42.364347 -71.104310    MA   
33                               North Cambridge  42.393327 -71.128370    MA   
34                                East Cambridge  42.370519 -71.084430    MA   
35                             Kendall Cambridge  42.362297 -71.084120    MA   
36                                    Somerville  42.381929 -71.099080    MA   
37                                    Somerville  42.399546 -71.121650    MA   
38                                    Somerville  42.390846 -71.092250    MA   
39                    North Brighton / Cambridge  42.367946 -71.120560    MA   
40                               Downtown Boston  42.338947 -70.919635    MA   
41                                    Prudential  42.347130 -71.082340    MA   
42                               Downtown Boston  42.338947 -70.919635    MA   
43                               Downtown Boston  42.350334 -71.053877    MA   
44                     South Boston / Fort Point  42.347974 -71.044630    MA   
45                   Kenmore / Boston University  42.346997 -71.102150    MA   
46                                     Brookline  42.324397 -71.139330    MA   
47                                     Brookline  42.344747 -71.121410    MA   
48                             Brookline Village  42.180048 -71.089230    MA   
49                                  

Finally, let's visualize the resulting clusters


In [106]:
# create map
map_clusters = folium.Map(location=[latitudeNYC, longitudeNYC], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Man_BosCam_merged['Latitude'], Man_BosCam_merged['Longitude'], Man_BosCam_merged['Neighborhood'], Man_BosCam_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### This map is depicting clusters in both Manhattan and Cambridge/Boston. As you can see, there are multiple clusters that have neighborhoods in both locations

#### Cluster 1

In [107]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 0, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue  \
18  Dorchester / Uphams Corner    MA                   Pub   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
18           Pizza Place                   Bar          Liquor Store   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
18     Food & Drink Shop           Flower Shop  Caribbean Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
18    Chinese Restaurant              Pharmacy    Fried Chicken Joint

#### Cluster 2


In [108]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 1, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue  \
4   Chinatown / Tufts-New England Medical Center    MA    Chinese Restaurant   
7                    West End / Back of the Hill    MA             Hotel Bar   
8                  Fenway / East Fens / Longwood    MA            Art Museum   
11                                     South End    MA             Gift Shop   
13                              Roxbury Crossing    MA           Pizza Place   
19                                      Mattapan    MA          Home Service   
23                                 Jamaica Plain    MA                Bakery   
27                                       Allston    MA     Korean Restaurant   
28                                      Brighton    MA                Bakery   
33                               North Cambridge    MA           Pizza Place   
34                                East Cambridge    MA        Sandwich Place   
35                             Kendall Cambridge    MA                  Café   
36                                    Somerville    MA           Pizza Place   
37                                    Somerville    MA           Pizza Place   
38                                    Somerville    MA           Pizza Place   
45                   Kenmore / Boston University    MA    Mexican Restaurant   
46                                     Brookline    MA           Pizza Place   
47                                     Brookline    MA           Pizza Place   
50                                     Chinatown    NY    Chinese Restaurant   
51                            Washington Heights    NY                  Café   
52                                        Inwood    NY    Mexican Restaurant   
53                              Hamilton Heights    NY           Pizza Place   
54                                Manhattanville    NY    Seafood Restaurant   
56                                   East Harlem    NY    Mexican Restaurant   
61                               Upper West Side    NY                  Café   
68                                  East Village    NY                   Bar   
69                               Lower East Side    NY    Chinese Restaurant   
71                                  Little Italy    NY                Bakery   
74                              Manhattan Valley    NY    Mexican Restaurant   
76                                      Gramercy    NY                   Bar   
85                                    Tudor City    NY                  Park   

   2nd Most Common Venue      3rd Most Common Venue  \
4                 Bakery           Asian Restaurant   
7    American Restaurant         Italian Restaurant   
8            Pizza Place                     Garden   
11                  Café  Latin American Restaurant   
13            Donut Shop         Italian Restaurant   
19           Pizza Place                     Bakery   
23           Coffee Shop                Pizza Place   
27       Thai Restaurant                     Bakery   
28           Pizza Place                       Bank   
33   Japanese Restaurant                 Hobby Shop   
34     Convenience Store                Coffee Shop   
35           Coffee Shop                 Food Truck   
36    Mexican Restaurant                       Park   
37    Mexican Restaurant                       Park   
38    Mexican Restaurant                       Park   
45   American Restaurant                       Café   
46             Gift Shop                       Park   
47             Gift Shop                       Park   
50                Bakery               Cocktail Bar   
51                Bakery          Mobile Phone Shop   
52                Lounge                       Café   
53           Coffee Shop                       Café   
54           Coffee Shop         Chinese Restaurant   
56                Bakery            Thai Restaurant   
61    Italian Restaurant                     Bakery   
68           Pizza Place          Korean Rest

#### Cluster 3


In [109]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 2, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue 2nd Most Common Venue  \
48  Brookline Village    MA               Stables           Flower Shop   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
48           Event Space               Exhibit    Falafel Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
48        Farmers Market  Fast Food Restaurant                 Field   

   9th Most Common Venue 10th Most Common Venue  
48   Filipino Restaurant            Fish Market

#### Cluster 4


In [110]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 3, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue 2nd Most Common Venue  \
30    Readville    MA      Business Service         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
30           Event Space               Exhibit    Falafel Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
30        Farmers Market  Fast Food Restaurant                 Field   

   9th Most Common Venue 10th Most Common Venue  
30   Filipino Restaurant            Fish Market

#### Cluster 5


In [111]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 4, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue 2nd Most Common Venue  \
12      Roxbury    MA   American Restaurant     Convenience Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
12                  Park    African Restaurant             BBQ Joint   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
12  Fast Food Restaurant      Business Service                  Café   

   9th Most Common Venue 10th Most Common Venue  
12         Women's Store            Flower Shop

#### Cluster 6

In [112]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 5, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue  \
15  Dorchester / Fields Corner    MA           Pizza Place   
17  Dorchester / Codman Square    MA                  Park   
20                South Boston    MA           Coffee Shop   
22                 Charlestown    MA           Yoga Studio   
24                  Roslindale    MA    Italian Restaurant   
25                West Roxbury    MA         Grocery Store   
29                   Hyde Park    MA   American Restaurant   
75         Morningside Heights    NY                  Park   
86             Stuyvesant Town    NY                  Park   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
15         Women's Store              Pharmacy    Seafood Restaurant   
17         Deli / Bodega           Yoga Studio  Caribbean Restaurant   
20           Pizza Place            Sports Bar          Liquor Store   
22     Convenience Store           Coffee Shop           Pizza Place   
24           Pizza Place   American Restaurant    Chinese Restaurant   
25              Pharmacy         Train Station                   Pub   
29    Chinese Restaurant        Sandwich Place              Pharmacy   
75   American Restaurant             Bookstore           Coffee Shop   
86                   Bar         Boat or Ferry           Coffee Shop   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
15                  Bank          Liquor Store        Sandwich Place   
17  Gym / Fitness Center         Grocery Store          Liquor Store   
20     Convenience Store          Gourmet Shop                  Park   
22              Pharmacy             Pet Store               Dog Run   
24                   Pub        Sandwich Place               Theater   
25                   Gym                  Bank        Clothing Store   
29           Gas Station        Discount Store          Liquor Store   
75          Burger Joint                  Café        Sandwich Place   
86       Harbor / Marina        Farmers Market  Gym / Fitness Center   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
15            Donut Shop               Dog Run              Pet Store  
17            Restaurant              Pharmacy         Farmers Market  
20    Mexican Restaurant                   Bar                   Bank  
22            Donut Shop          Liquor Store          Shopping Mall  
24                   Bar         Grocery Store       Greek Restaurant  
25          Liquor Store           Pizza Place        Automotive Shop  
29        Clothing Store     Convenience Store            Pizza Place  
75    Seafood Restaurant           Salad Place           Liquor Store  
86              Fountain           Gas Station             Playground

#### Cluster 7

In [113]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 6, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue 2nd Most Common Venue  \
14  Roxbury / Grove Hall    MA         Shopping Mall  Fast Food Restaurant   

   3rd Most Common Venue 4th Most Common Venue  \
14  Caribbean Restaurant        Cosmetics Shop   

              5th Most Common Venue 6th Most Common Venue  \
14  Southern / Soul Food Restaurant             Nightclub   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
14           Supermarket        Clothing Store            Donut Shop   

   10th Most Common Venue  
14               Pharmacy

#### Cluster 8

In [114]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 7, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue 2nd Most Common Venue  \
2   Markets / Inner Harbor    MA    Italian Restaurant    Seafood Restaurant   
6                North End    MA    Italian Restaurant           Pizza Place   
21             East Boston    MA    Italian Restaurant    Chinese Restaurant   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2                      Bakery                  Park         Historic Site   
6                 Coffee Shop    Seafood Restaurant                 Hotel   
21  Latin American Restaurant  Brazilian Restaurant     Convenience Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2                   Café           Pizza Place        Sandwich Place   
6                 Bakery        Sandwich Place                  Park   
21            Donut Shop                Bakery    Mexican Restaurant   

   9th Most Common Venue      10th Most Common Venue  
2                  Hotel  Tourist Information Center  
6          Historic Site               Grocery Store  
21        Shipping Store               Metro Station

#### Cluster 9

In [115]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 8, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State          1st Most Common Venue  \
0                Downtown Boston    MA               Business Service   
1                    Beacon Hill    MA            American Restaurant   
3   Financial District / Wharves    MA                  Boat or Ferry   
5                Downtown Boston    MA               Business Service   
9                       Back Bay    MA                            Spa   
10               Downtown Boston    MA               Business Service   
16               Downtown Boston    MA               Business Service   
26               Downtown Boston    MA               Business Service   
32           The Port, Cambridge    MA  Vegetarian / Vegan Restaurant   
39    North Brighton / Cambridge    MA            Japanese Restaurant   
40               Downtown Boston    MA               Business Service   
41                    Prudential    MA                 Clothing Store   
42               Downtown Boston    MA               Business Service   
43               Downtown Boston    MA               Business Service   
44     South Boston / Fort Point    MA                     Restaurant   
49                   Marble Hill    NY                            Gym   
55                Central Harlem    NY             African Restaurant   
57               Upper East Side    NY                        Exhibit   
58                     Yorkville    NY             Italian Restaurant   
59                    Lenox Hill    NY             Italian Restaurant   
60              Roosevelt Island    NY                           Park   
62                Lincoln Square    NY                           Café   
63                       Clinton    NY             Italian Restaurant   
64                       Midtown    NY                          Hotel   
65                   Murray Hill    NY                    Coffee Shop   
66                       Chelsea    NY                    Art Gallery   
67             Greenwich Village    NY             Italian Restaurant   
70                       Tribeca    NY                           Park   
72                          Soho    NY                 Clothing Store   
73                  West Village    NY             Italian Restaurant   
77             Battery Park City    NY                    Coffee Shop   
78            Financial District    NY                    Coffee Shop   
79                 Carnegie Hill    NY                    Coffee Shop   
80                          Noho    NY             Italian Restaurant   
81                  Civic Center    NY                    Coffee Shop   
82                 Midtown South    NY              Korean Restaurant   
83                  Sutton Place    NY             Italian Restaurant   
84                    Turtle Bay    NY             Italian Restaurant   
87                      Flatiron    NY             Italian Restaurant   
88                  Hudson Yards    NY           Gym / Fitness Center   

   2nd Most Common Venue    3rd Most Common Venue     4th Most Common Venue  \
0    Rental Car Location              Coffee Shop       American Restaurant   
1   Gym / Fitness Center               Steakhouse   New American Restaurant   
3        Harbor / Marina                    Hotel                  Aquarium   
5    Rental Car Location              Coffee Shop       American Restaurant   
9                    Gym           Cosmetics Shop               Coffee Shop   
10   Rental Car Location              Coffee Shop       American Restaurant   
16   Rental Car Location              Coffee Shop       American Restaurant   
26   Rental Car Location              Coffee Shop       American Restaurant   
32           Coffee Shop                      Bar              Cocktail Bar   
39  Gym / Fitness Center                     Park               Pizza Place   
40   Rental Car Location              Coffee Shop       American Restaurant   
41    Italian Restaurant              Coffee Shop        Seafood Restaurant   

#### Cluster 10

In [116]:
Man_BosCam_merged.loc[Man_BosCam_merged['Cluster Labels'] == 9, Man_BosCam_merged.columns[[0] + [3] + list(range(5, Man_BosCam_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue 2nd Most Common Venue  \
31  Mid Cambridge    MA   American Restaurant                Bakery   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
31    Italian Restaurant                  Park         Grocery Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
31            Restaurant                 Hotel           Pizza Place   

   9th Most Common Venue 10th Most Common Venue  
31         Historic Site                  Field

### The Port is part of Cluster 9 along with neighborhoods in both Cambridge/Boston and Manhattan. Similar to my analysis of cluster 2 for only the Boston/Cambridge area, this cluster is also categorized by having lots of restaurants, shops, and fitness centers/gyms. Thus, these are neighborhoods that often receive visitors, where people work, and where people live to be in close proximity to gyms and a wide variety of restaurants.

### However, seeing as this cluster has a considerable number of members, I will do an additional clustering analysis to narrow down this list.

## Clustering Analysis No.4: The Port Cambridge and Manhattan neighborhoods in same cluster.

To perform the last clustering analysis, I will be only including The Port and the Manhattan neighborhoods that were in the same cluster in the previous clustering analysis as The Port

## 1. Prepare Data

In [137]:
#Creating new data frame with only members of the cluster where The Port is in
Man_BosCamCluster = Man_BosCam_merged[Man_BosCam_merged['Cluster Labels']==8]
Man_BosCamCluster

Neighborhood   Latitude  Longitude State  Cluster Labels  \
0                Downtown Boston  42.370567 -71.026964    MA               8   
1                    Beacon Hill  42.357903 -71.064080    MA               8   
3   Financial District / Wharves  42.356532 -71.053650    MA               8   
5                Downtown Boston  42.338947 -70.919635    MA               8   
9                       Back Bay  42.349622 -71.073720    MA               8   
10               Downtown Boston  42.338947 -70.919635    MA               8   
16               Downtown Boston  42.338947 -70.919635    MA               8   
26               Downtown Boston  42.338947 -70.919635    MA               8   
32           The Port, Cambridge  42.364347 -71.104310    MA               8   
39    North Brighton / Cambridge  42.367946 -71.120560    MA               8   
40               Downtown Boston  42.338947 -70.919635    MA               8   
41                    Prudential  42.347130 -71.082340    MA               8   
42               Downtown Boston  42.338947 -70.919635    MA               8   
43               Downtown Boston  42.350334 -71.053877    MA               8   
44     South Boston / Fort Point  42.347974 -71.044630    MA               8   
49                   Marble Hill  40.876551 -73.910660    NY               8   
55                Central Harlem  40.815976 -73.943211    NY               8   
57               Upper East Side  40.775639 -73.960508    NY               8   
58                     Yorkville  40.775930 -73.947118    NY               8   
59                    Lenox Hill  40.768113 -73.958860    NY               8   
60              Roosevelt Island  40.762160 -73.949168    NY               8   
62                Lincoln Square  40.773529 -73.985338    NY               8   
63                       Clinton  40.759101 -73.996119    NY               8   
64                       Midtown  40.754691 -73.981669    NY               8   
65                   Murray Hill  40.748303 -73.978332    NY               8   
66                       Chelsea  40.744035 -74.003116    NY               8   
67             Greenwich Village  40.726933 -73.999914    NY               8   
70                       Tribeca  40.721522 -74.010683    NY               8   
72                          Soho  40.722184 -74.000657    NY               8   
73                  West Village  40.734434 -74.006180    NY               8   
77             Battery Park City  40.711932 -74.016869    NY               8   
78            Financial District  40.707107 -74.010665    NY               8   
79                 Carnegie Hill  40.782683 -73.953256    NY               8   
80                          Noho  40.723259 -73.988434    NY               8   
81                  Civic Center  40.715229 -74.005415    NY               8   
82                 Midtown South  40.748510 -73.988713    NY               8   
83                  Sutton Place  40.760280 -73.963556    NY               8   
84                    Turtle Bay  40.752042 -73.967708    NY               8   
87                      Flatiron  40.739673 -73.990947    NY               8   
88                  Hudson Yards  40.756658 -74.000111    NY               8   

            1st Most Common Venue 2nd Most Common Venue  \
0                Business Service   Rental Car Location   
1             American Restaurant  Gym / Fitness Center   
3                   Boat or Ferry       Harbor / Marina   
5                Business Service   Rental Car Location   
9                             Spa                   Gym   
10               Business Service   Rental Car Location   
16               Business Service   Rental Car Location   
26               Business Service   Rental Car Location   
32  Vegetarian / Vegan Restaurant           Coffee Shop   
39            Japanese Restaurant  Gym / Fitness Center   
40               Business Service   Rental Car Location   
41                 Clothing Sto

In [138]:
#Filtering the dataframe to only have neighboorhoods in Manhattan ot The Port
Man_BosCamCluster = Man_BosCamCluster[(Man_BosCamCluster['State'] == 'NY') | (Man_BosCamCluster['Neighborhood'] == 'The Port, Cambridge')].reset_index(drop=True)
Man_BosCamCluster

Neighborhood   Latitude  Longitude State  Cluster Labels  \
0   The Port, Cambridge  42.364347 -71.104310    MA               8   
1           Marble Hill  40.876551 -73.910660    NY               8   
2        Central Harlem  40.815976 -73.943211    NY               8   
3       Upper East Side  40.775639 -73.960508    NY               8   
4             Yorkville  40.775930 -73.947118    NY               8   
5            Lenox Hill  40.768113 -73.958860    NY               8   
6      Roosevelt Island  40.762160 -73.949168    NY               8   
7        Lincoln Square  40.773529 -73.985338    NY               8   
8               Clinton  40.759101 -73.996119    NY               8   
9               Midtown  40.754691 -73.981669    NY               8   
10          Murray Hill  40.748303 -73.978332    NY               8   
11              Chelsea  40.744035 -74.003116    NY               8   
12    Greenwich Village  40.726933 -73.999914    NY               8   
13              Tribeca  40.721522 -74.010683    NY               8   
14                 Soho  40.722184 -74.000657    NY               8   
15         West Village  40.734434 -74.006180    NY               8   
16    Battery Park City  40.711932 -74.016869    NY               8   
17   Financial District  40.707107 -74.010665    NY               8   
18        Carnegie Hill  40.782683 -73.953256    NY               8   
19                 Noho  40.723259 -73.988434    NY               8   
20         Civic Center  40.715229 -74.005415    NY               8   
21        Midtown South  40.748510 -73.988713    NY               8   
22         Sutton Place  40.760280 -73.963556    NY               8   
23           Turtle Bay  40.752042 -73.967708    NY               8   
24             Flatiron  40.739673 -73.990947    NY               8   
25         Hudson Yards  40.756658 -74.000111    NY               8   

            1st Most Common Venue 2nd Most Common Venue  \
0   Vegetarian / Vegan Restaurant           Coffee Shop   
1                             Gym        Sandwich Place   
2              African Restaurant        Cosmetics Shop   
3                         Exhibit           Coffee Shop   
4              Italian Restaurant           Coffee Shop   
5              Italian Restaurant          Cocktail Bar   
6                            Park           Dry Cleaner   
7                            Café                 Plaza   
8              Italian Restaurant  Gym / Fitness Center   
9                           Hotel        Clothing Store   
10                    Coffee Shop                 Hotel   
11                    Art Gallery           Coffee Shop   
12             Italian Restaurant        Clothing Store   
13                           Park   American Restaurant   
14                 Clothing Store    Italian Restaurant   
15             Italian Restaurant          Cocktail Bar   
16                    Coffee Shop        Clothing Store   
17                    Coffee Shop           Pizza Place   
18                    Coffee Shop                  Café   
19             Italian Restaurant           Art Gallery   
20                    Coffee Shop  Gym / Fitness Center   
21              Korean Restaurant                 Hotel   
22             Italian Restaurant           Coffee Shop   
23             Italian Restaurant           Coffee Shop   
24             Italian Restaurant   Japanese Restaurant   
25           Gym / Fitness Center    Italian Restaurant   

      3rd Most Common Venue     4th Most Common Venue 5th Most Common Venue  \
0                       Bar              Cocktail Bar                 Plaza   
1               Coffee Shop            Discount Store           Yoga Studio   
2       American Restaurant         French Restaurant    Chinese Restaurant   
3        Italian Restaurant      Gym / Fitness Center                Bakery   
4                       Bar                       Gym         Deli / Bodega   
5               Coffee Sh

## 2. Analyzing neighboorhhods

In [139]:
Cluster_venues = getNearbyVenues(names=Man_BosCamCluster['Neighborhood'],
                                   latitudes=Man_BosCamCluster['Latitude'],
                                   longitudes=Man_BosCamCluster['Longitude']
                                  )

The Port, Cambridge
Marble Hill
Central Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
Tribeca
Soho
West Village
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Flatiron
Hudson Yards


#### Let's check the size of the resulting dataframe


In [140]:
print(Cluster_venues.shape)
Cluster_venues.head()

(2242, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  The Port, Cambridge              42.364347               -71.10431   
1  The Port, Cambridge              42.364347               -71.10431   
2  The Port, Cambridge              42.364347               -71.10431   
3  The Port, Cambridge              42.364347               -71.10431   
4  The Port, Cambridge              42.364347               -71.10431   

                Venue  Venue Latitude  Venue Longitude Venue Category  
0   The Dance Complex       42.364313       -71.102005   Dance Studio  
1  Rodney's Bookstore       42.365967       -71.104659      Bookstore  
2    Prana Power Yoga       42.364926       -71.102815    Yoga Studio  
3              H Mart       42.364936       -71.102740    Supermarket  
4      Brick & Mortar       42.364924       -71.102373   Cocktail Bar

Let's check how many venues were returned for each neighborhood


In [141]:
Cluster_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       76                      76     76   
Carnegie Hill                           86                      86     86   
Central Harlem                          43                      43     43   
Chelsea                                100                     100    100   
Civic Center                           100                     100    100   
Clinton                                100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Greenwich Village                      100                     100    100   
Hudson Yards                            69                      69     69   
Lenox Hill                             100                     100    100   
Lincoln Square                          93                      93     93   
Marble Hill                             24                      24     24   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Murray Hill                            100                     100    100   
Noho                                   100                     100    100   
Roosevelt Island                        27                      27     27   
Soho                                   100                     100    100   
Sutton Place                           100                     100    100   
The Port, Cambridge                     40                      40     40   
Tribeca                                 84                      84     84   
Turtle Bay                             100                     100    100   
Upper East Side                        100                     100    100   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                76               76              76  
Carnegie Hill                    86               86              86  
Central Harlem                   43               43              43  
Chelsea                         100              100             100  
Civic Center                    100              100             100  
Clinton                         100              100             100  
Financial District              100              100             100  
Flatiron                        100              100             100  
Greenwich Village               100              100             100  
Hudson Yards                     69               69              69  
Lenox Hill                      100              100             100  
Lincoln Square                   93               93              93  
Marble Hill                      24               24              24  
Midtown                         100              100             100  
Midtown South                   100              100             100  
Murray Hill                     100              100             100  
Noho                            100              100             100  
Roosevelt Island                 27               27              27  
Soho                            100              100             100  
Sutton Place                    100              100             100  
The Port, Cambridge              40               40              40  
Tribeca                          84               84              84  
Turtle Bay                      100              100             100  
Upper East Side                 100              100             100  
West Village      

#### Let's find out how many unique categories can be curated from all the returned venues


In [142]:
print('There are {} uniques categories.'.format(len(Cluster_venues['Venue Category'].unique())))

There are 299 uniques categories.


In [143]:
# one hot encoding
Cluster_onehot = pd.get_dummies(Cluster_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Cluster_onehot['Neighborhood'] = Cluster_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Cluster_onehot.columns[-1]] + list(Cluster_onehot.columns[:-1])
Cluster_onehot = Cluster_onehot[fixed_columns]

Cluster_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  The Port, Cambridge                  0               0                  0   
1  The Port, Cambridge                  0               0                  0   
2  The Port, Cambridge                  0               0                  0   
3  The Port, Cambridge                  0               0                  0   
4  The Port, Cambridge                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  \
0                   0                    0             0   
1                   0                    0             0   
2                   0                    0             0   
3                   0                    0             0   
4                   0                    0             0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                    0          0           0           0       0     0    0   
1                    0          0           0           0       0     0    0   
2                    0          0           0           0       0     0    0   
3                    0          0           0           0       0     0    0   
4                    0          0           0           0       0     0    0   

   Basketball Court  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                 0         0            0           0              0   
1                 0         0            0           0              0   
2                 0         0            0           0              0   
3                 0         0            0           0              0   
4                 0         0            0           0              0   

   Bike Rental / Bike Share  Bike Trail  Bistro  Board Shop  Boat or Ferry  \
0                         0           0       0           0              0   
1                         0           0       0           0              0   
2                         0           0       0           0              0   
3                         0           0       0           0              0   
4                         0           0       0           0              0   

   Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  Breakfast Spot  \
0          0         0           0                     0               0   
1          1         0           0                     0               0   
2          0         0           0                     0               0   
3          0         0           0                     0               0   
4          0         0           0                     0               0   

   Bridal Shop  Bridge  Bubble Tea Shop  Building  Burger Joint  \
0            0       0                0         0             0   
1            0       0                0         0             0   
2            0       0                0         0             0   
3            0       0                0         0             0   
4            0       0                0         0             0   


And let's examine the new dataframe size.


In [144]:
Cluster_onehot.shape

(2242, 300)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category


In [145]:
Cluster_grouped = Cluster_onehot.groupby('Neighborhood').mean().reset_index()
Cluster_grouped

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City               0.00            0.00               0.00   
1         Carnegie Hill               0.00            0.00               0.00   
2        Central Harlem               0.00            0.00               0.00   
3               Chelsea               0.00            0.00               0.00   
4          Civic Center               0.00            0.00               0.00   
5               Clinton               0.00            0.00               0.00   
6    Financial District               0.00            0.00               0.00   
7              Flatiron               0.00            0.00               0.00   
8     Greenwich Village               0.01            0.00               0.00   
9          Hudson Yards               0.00            0.00               0.00   
10           Lenox Hill               0.00            0.00               0.01   
11       Lincoln Square               0.00            0.00               0.00   
12          Marble Hill               0.00            0.00               0.00   
13              Midtown               0.00            0.00               0.00   
14        Midtown South               0.00            0.00               0.00   
15          Murray Hill               0.00            0.00               0.00   
16                 Noho               0.00            0.00               0.00   
17     Roosevelt Island               0.00            0.00               0.00   
18                 Soho               0.00            0.00               0.00   
19         Sutton Place               0.00            0.01               0.00   
20  The Port, Cambridge               0.00            0.00               0.00   
21              Tribeca               0.00            0.00               0.00   
22           Turtle Bay               0.00            0.00               0.00   
23      Upper East Side               0.00            0.00               0.00   
24         West Village               0.01            0.01               0.00   
25            Yorkville               0.00            0.00               0.00   

    African Restaurant  American Restaurant  Antique Shop  \
0             0.000000             0.013158          0.00   
1             0.000000             0.011628          0.00   
2             0.069767             0.046512          0.00   
3             0.000000             0.040000          0.00   
4             0.000000             0.040000          0.01   
5             0.000000             0.040000          0.00   
6             0.000000             0.030000          0.00   
7             0.000000             0.030000          0.00   
8             0.000000             0.030000          0.00   
9             0.000000             0.057971          0.00   
10            0.000000             0.000000          0.00   
11            0.000000             0.021505          0.00   
12            0.000000             0.041667          0.00   
13            0.000000             0.030000          0.00   
14            0.000000             0.020000          0.00   
15            0.000000             0.030000          0.00   
16            0.000000             0.010000          0.00   
17            0.000000             0.000000          0.00   
18            0.000000             0.010000          0.00   
19            0.000000             0.030000          0.00   
20            0.000000             0.025000          0.00   
21            0.000000             0.047619          0.00   
22            0.000000             0.010000          0.00   
23            0.000000             0.040000          0.00   
24            0.000000             0.040000          0.00   
25            0.000000             0.000000          0.00   

    Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                 0.000000     0.000000    0.000000                0.000   
1                 0.011

In [146]:
Cluster_grouped.shape

(26, 300)

#### Let's print each neighborhood along with the top 5 most common venues


In [147]:
num_top_venues = 5

for hood in Cluster_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = Cluster_grouped[Cluster_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
            venue  freq
0     Coffee Shop  0.07
1             Gym  0.05
2  Clothing Store  0.05
3            Park  0.05
4           Hotel  0.05


----Carnegie Hill----
               venue  freq
0        Coffee Shop  0.08
1     Cosmetics Shop  0.05
2               Café  0.05
3  French Restaurant  0.03
4        Pizza Place  0.03


----Central Harlem----
                 venue  freq
0   African Restaurant  0.07
1  American Restaurant  0.05
2                  Bar  0.05
3   Seafood Restaurant  0.05
4    French Restaurant  0.05


----Chelsea----
                 venue  freq
0          Art Gallery  0.06
1          Coffee Shop  0.05
2               Bakery  0.05
3  American Restaurant  0.04
4       Ice Cream Shop  0.03


----Civic Center----
                  venue  freq
0           Coffee Shop  0.08
1          Cocktail Bar  0.04
2   American Restaurant  0.04
3                   Spa  0.04
4  Gym / Fitness Center  0.04


----Clinton----
                  venue  freq
0 

Now let's create the new dataframe and display the top 10 venues for each neighborhood.


In [148]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = Cluster_grouped['Neighborhood']

for ind in np.arange(Cluster_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Cluster_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City           Coffee Shop                  Park   
1      Carnegie Hill           Coffee Shop        Cosmetics Shop   
2     Central Harlem    African Restaurant    Chinese Restaurant   
3            Chelsea           Art Gallery           Coffee Shop   
4       Civic Center           Coffee Shop          Cocktail Bar   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                 Hotel                   Gym        Clothing Store   
1                  Café           Yoga Studio             Wine Shop   
2                   Bar     French Restaurant   American Restaurant   
3                Bakery   American Restaurant        Ice Cream Shop   
4   American Restaurant                 Hotel                   Spa   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Boat or Ferry         Memorial Site          Burger Joint   
1           Pizza Place             Bookstore                   Gym   
2    Seafood Restaurant        Cosmetics Shop              Boutique   
3                 Hotel    Seafood Restaurant      Sushi Restaurant   
4  Gym / Fitness Center           Yoga Studio     French Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0            Food Court           Gourmet Shop  
1     French Restaurant                    Bar  
2                   Gym                Library  
3        Cosmetics Shop                    Bar  
4                  Park                 Bakery

## 3. Cluster Neighborhoods


Run _k_-means to cluster the neighborhood into 5 clusters.


In [149]:
# set number of clusters
kclusters = 5

Cluster_grouped_clustering = Cluster_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Cluster_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 1, 2, 2, 2, 1, 1, 1, 1, 1], dtype=int32)

In [150]:
Man_BosCamCluster1 = Man_BosCamCluster[['Neighborhood','Latitude','Longitude','State']]
Man_BosCamCluster1.head()

Neighborhood   Latitude  Longitude State
0  The Port, Cambridge  42.364347 -71.104310    MA
1          Marble Hill  40.876551 -73.910660    NY
2       Central Harlem  40.815976 -73.943211    NY
3      Upper East Side  40.775639 -73.960508    NY
4            Yorkville  40.775930 -73.947118    NY

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.


In [151]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Cluster_merged = Man_BosCamCluster1

# merge manhattan_grouped with Man_BosCamCluster1 to add latitude/longitude for each neighborhood
Cluster_merged = Cluster_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

Cluster_merged.head() # check the last columns!

Neighborhood   Latitude  Longitude State  Cluster Labels  \
0  The Port, Cambridge  42.364347 -71.104310    MA               2   
1          Marble Hill  40.876551 -73.910660    NY               3   
2       Central Harlem  40.815976 -73.943211    NY               2   
3      Upper East Side  40.775639 -73.960508    NY               1   
4            Yorkville  40.775930 -73.947118    NY               1   

           1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  Vegetarian / Vegan Restaurant                   Bar          Cocktail Bar   
1                            Gym        Discount Store        Sandwich Place   
2             African Restaurant    Chinese Restaurant                   Bar   
3                        Exhibit           Coffee Shop    Italian Restaurant   
4             Italian Restaurant           Coffee Shop                   Bar   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0           Coffee Shop           Yoga Studio          Dance Studio   
1           Coffee Shop           Yoga Studio           Pizza Place   
2     French Restaurant   American Restaurant    Seafood Restaurant   
3                Bakery  Gym / Fitness Center   American Restaurant   
4                   Gym         Deli / Bodega      Sushi Restaurant   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0             Bookstore        Breakfast Spot   Shanghai Restaurant   
1            Steakhouse         Shopping Mall    Seafood Restaurant   
2        Cosmetics Shop              Boutique                   Gym   
3           Pizza Place     French Restaurant             Juice Bar   
4             Wine Shop   Japanese Restaurant        Ice Cream Shop   

  10th Most Common Venue  
0         Sandwich Place  
1               Pharmacy  
2                Library  
3                    Spa  
4            Pizza Place

Finally, let's visualize the resulting clusters


In [152]:
# create map
map_clusters = folium.Map(location=[latitudeNYC, longitudeNYC], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Cluster_merged['Latitude'], Cluster_merged['Longitude'], Cluster_merged['Neighborhood'], Cluster_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

I tested different number of clusters to ensure with be clustered with other Manhattan neighbood, which is depicted in the map.

### Cluster 1

In [153]:
Cluster_merged.loc[Cluster_merged['Cluster Labels'] == 0, Cluster_merged.columns[[0] + [3] + list(range(5, Cluster_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue 2nd Most Common Venue  \
6  Roosevelt Island    NY                  Park           Coffee Shop   

  3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
6  Gym / Fitness Center  Outdoors & Recreation      Greek Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
6           Dry Cleaner          Liquor Store        Sandwich Place   

  9th Most Common Venue 10th Most Common Venue  
6        Scenic Lookout            Supermarket

### Cluster 2

In [154]:
Cluster_merged.loc[Cluster_merged['Cluster Labels'] == 1, Cluster_merged.columns[[0] + [3] + list(range(5, Cluster_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue    2nd Most Common Venue  \
3      Upper East Side    NY               Exhibit              Coffee Shop   
4            Yorkville    NY    Italian Restaurant              Coffee Shop   
5           Lenox Hill    NY    Italian Restaurant              Pizza Place   
8              Clinton    NY    Italian Restaurant     Gym / Fitness Center   
10         Murray Hill    NY           Coffee Shop                    Hotel   
12   Greenwich Village    NY    Italian Restaurant           Clothing Store   
14                Soho    NY        Clothing Store       Italian Restaurant   
15        West Village    NY    Italian Restaurant  New American Restaurant   
17  Financial District    NY           Coffee Shop              Pizza Place   
18       Carnegie Hill    NY           Coffee Shop           Cosmetics Shop   
19                Noho    NY    Italian Restaurant              Art Gallery   
22        Sutton Place    NY           Coffee Shop                     Park   
23          Turtle Bay    NY    Italian Restaurant              Coffee Shop   
24            Flatiron    NY    Italian Restaurant  New American Restaurant   
25        Hudson Yards    NY  Gym / Fitness Center                    Hotel   

   3rd Most Common Venue   4th Most Common Venue     5th Most Common Venue  \
3     Italian Restaurant                  Bakery      Gym / Fitness Center   
4                    Bar                     Gym             Deli / Bodega   
5           Cocktail Bar             Coffee Shop          Sushi Restaurant   
8            Coffee Shop     American Restaurant                   Theater   
10        Sandwich Place                     Bar       Japanese Restaurant   
12      Sushi Restaurant     American Restaurant         Indian Restaurant   
14           Coffee Shop                Boutique  Mediterranean Restaurant   
15          Cocktail Bar     American Restaurant                      Park   
17                   Bar            Cocktail Bar        Italian Restaurant   
18                  Café             Yoga Studio                 Wine Shop   
19     French Restaurant             Coffee Shop               Pizza Place   
22    Italian Restaurant  Furniture / Home Store                       Gym   
23      Sushi Restaurant     Japanese Restaurant        Seafood Restaurant   
24   Japanese Restaurant    Gym / Fitness Center                       Spa   
25    Italian Restaurant     American Restaurant                      Café   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
3    American Restaurant           Pizza Place     French Restaurant   
4       Sushi Restaurant             Wine Shop   Japanese Restaurant   
5   Gym / Fitness Center                   Gym          Burger Joint   
8         Sandwich Place             Wine Shop                   Spa   
10          Burger Joint  Gym / Fitness Center   American Restaurant   
12                   Gym              Boutique          Dessert Shop   
14                Bakery          Optical Shop   Sporting Goods Shop   
15               Theater        Ice Cream Shop              Wine Bar   
17                  Café           Salad Place   American Restaurant   
18           Pizza Place             Bookstore                   Gym   
19                Bakery         Grocery Store    Mexican Restaurant   
22  Gym / Fitness Center           Pizza Place   American Restaurant   
23         Deli / Bodega      Ramen Restaurant                  Park   
24             Wine Shop           Coffee Shop   American Restaurant   
25                  Park                   Bar                   Gym   

     9th Most Common Venue 10th Most Common Venue  
3                Juice Bar                    Spa  
4           Ice Cream Shop            Pizza Place  
5                     Café     Salon / Barbershop  
8                      Gym                  Hotel  
10             Pizza Place                    Pub  
12                    Café     

### Cluster 3

In [155]:
Cluster_merged.loc[Cluster_merged['Cluster Labels'] == 2, Cluster_merged.columns[[0] + [3] + list(range(5, Cluster_merged.shape[1]))]]

Neighborhood State          1st Most Common Venue  \
0   The Port, Cambridge    MA  Vegetarian / Vegan Restaurant   
2        Central Harlem    NY             African Restaurant   
7        Lincoln Square    NY                          Plaza   
9               Midtown    NY                          Hotel   
11              Chelsea    NY                    Art Gallery   
13              Tribeca    NY                           Park   
16    Battery Park City    NY                    Coffee Shop   
20         Civic Center    NY                    Coffee Shop   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                    Bar          Cocktail Bar           Coffee Shop   
2     Chinese Restaurant                   Bar     French Restaurant   
7                   Café               Theater          Concert Hall   
9         Clothing Store               Theater   Sporting Goods Shop   
11           Coffee Shop                Bakery   American Restaurant   
13   American Restaurant    Italian Restaurant           Coffee Shop   
16                  Park                 Hotel                   Gym   
20          Cocktail Bar   American Restaurant                 Hotel   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0             Yoga Studio          Dance Studio             Bookstore   
2     American Restaurant    Seafood Restaurant        Cosmetics Shop   
7   Performing Arts Venue  Gym / Fitness Center    Italian Restaurant   
9          Sandwich Place   American Restaurant            Steakhouse   
11         Ice Cream Shop                 Hotel    Seafood Restaurant   
13                    Spa                  Café              Wine Bar   
16         Clothing Store         Boat or Ferry         Memorial Site   
20                    Spa  Gym / Fitness Center           Yoga Studio   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0         Breakfast Spot   Shanghai Restaurant         Sandwich Place  
2               Boutique                   Gym                Library  
7              Wine Shop     French Restaurant    Indie Movie Theater  
9            Coffee Shop                   Spa                 Bakery  
11      Sushi Restaurant        Cosmetics Shop                    Bar  
13            Poke Place            Skate Park             Playground  
16          Burger Joint            Food Court           Gourmet Shop  
20     French Restaurant                  Park                 Bakery

### Cluster 4

In [156]:
Cluster_merged.loc[Cluster_merged['Cluster Labels'] == 3, Cluster_merged.columns[[0] + [3] + list(range(5, Cluster_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue 2nd Most Common Venue  \
1  Marble Hill    NY                   Gym        Discount Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
1        Sandwich Place           Coffee Shop           Yoga Studio   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
1           Pizza Place            Steakhouse         Shopping Mall   

  9th Most Common Venue 10th Most Common Venue  
1    Seafood Restaurant               Pharmacy

### Cluster 5

In [157]:
Cluster_merged.loc[Cluster_merged['Cluster Labels'] == 4, Cluster_merged.columns[[0] + [3] + list(range(5, Cluster_merged.shape[1]))]]

Neighborhood State 1st Most Common Venue 2nd Most Common Venue  \
21  Midtown South    NY     Korean Restaurant                 Hotel   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
21             Hotel Bar   Japanese Restaurant          Dessert Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
21           Coffee Shop        Cosmetics Shop  Gym / Fitness Center   

   9th Most Common Venue 10th Most Common Venue  
21           Salad Place         Clothing Store

## Conclusions

### The Port is in Cluster 3, which means the other neighborhoods in this clusters are deemed as similar neighborhoods to The Port and, hence, potential neighborhood I could move to. As we have seen throughout this project, The Port is a neighborhood with a wide range of restaurants, gyms/fitness centers, hotels, and car rentals. All of these are common trends along the other neighborhoods in this cluster and confirm my analysis. These neighborhoods are good for people, like me, who like going out to eat, work out, live close to their place of work, and have places nearby where friends or family can stay when visiting.

### This project is flexible and could be used if someone wanted to move within the same city or move to a different city that New York within the US. Given that I have all the coordinates for all zip codes in the US, the only data source missing would be the list of neighborhoods to be able to run this analysis.

## Recommendations

### If I were to advance this analysis, I would use some techniques to optimize the number of clusters instead of trying different ones one by one. Also, I would like to include other relevant data such as median rent prices, crime rate, etc. that would help me do an even better analysis.